#1. 기본 설정

- 예전거

In [0]:
%pip install --quiet selenium==4.21.0 webdriver-manager==4.0.2 beautifulsoup4==4.12.3 lxml==5.2.2 pandas==2.2.2
dbutils.library.restartPython()

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
import os, re, json, time, random, pandas as pd
from urllib.parse import urljoin
from bs4 import BeautifulSoup
from datetime import datetime, timezone, timedelta
from pyspark.sql import functions as F
from pyspark.sql import types as T

from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException
from webdriver_manager.chrome import ChromeDriverManager

---------------------------------------------------------------------------
ModuleNotFoundError                       Traceback (most recent call last)
File <command-8079581274089994>, line 8
      5 from pyspark.sql import functions as F
      6 from pyspark.sql import types as T
----> 8 from selenium import webdriver
      9 from selenium.webdriver.chrome.options import Options
     10 from selenium.webdriver.chrome.service import Service

ModuleNotFoundError: No module named 'selenium'

In [0]:
import re
import time
import random
from datetime import datetime
from typing import Dict, Any, Optional

import numpy as np
import pandas as pd
import pytz
import requests
from bs4 import BeautifulSoup

from pyspark.sql import SparkSession
from delta.tables import DeltaTable

# 2. 크롤링 + 적재

## 0) 기본설정

### 공고 ID 불러오기

In [0]:
path = f"/dbfs/FileStore/jumpit_positions_all.csv" #추후 파일명 수정 필요
pdf = pd.read_csv(path)
display(pdf)

posting_title company_name hiring_bonus posting_tech_stack responsibilities minimum_qualifications preferred_qualifications posting_benefits hiring_process experience education deadline work_location posting_url posting_id company_url job_category 백엔드 경력 채용 (6~9년) 텐빌리언 💰 취업축하금 50만원 Git, Spring Boot, DB • API 연동 / 오픈 소스 라이브러리 
• 프론트엔드 개발자 협업 업무
• 신규 플랫폼 개발
• Client 사이트 신규 개발
• 사이트 유지 보수 및 성능 개선 • 관련 경험 6~9년
• Backend 개발자 경험자 
• Composer 경험자
• 버전 관리 시스템 활용 가능자
• PHP 개발 경험자 • 프론트엔드 개발 언어 이해도 필요
• 워드프레스 개발 경험 
• SEO 기술 활용자 -자유로운 환경의 업무 스타일
-자유로운 연차 사용 및 시차 출퇴근
-생일 연차, 장기근속 포상금, 리조트 회원권 지원
-점심식사 및 연 1회 건강검진 지원 서류 전형 > 면접 > 최종 합격 경력 6~9년 대학교졸업(4년) 이상 2025-09-16 서울 구로구 구로동 1127-26 지도보기 · 주소복사 https://jumpit.saramin.co.kr/position/51583665 5.1583665E7 https://jumpit.saramin.co.kr/company/MTYwMDgwMTk4NQ==?company_nm=텐빌리언 1 백엔드 개발자(웹,인프라) 에피소든 💰 취업축하금 50만원 TypeScript, NestJS, PostgreSQL 자세한 내용은
team.episoden.com (http://team.episoden.com)
을 참고해 주세요.

[글로벌 서비스 Episoden]
에피소든은 2분안에 외국인을 만나서 영어로 이야기할 수 있게 해주는 화상대화 서비스입니다. 
지난 3년간 빠르게 성장하여, 164개국 이상에서 사용하는 글로벌 서비스로 성장해 왔습니다. 
전 세계를 대상으로 안정적으로 서비스를 해 나가는 쉽지 않은 일을 저희와 함께 만들어가실, 괴수 개발자를 찾고 있습니다.

[Episoden의 개발자를 모십니다]
• 개발하는 것을 무엇보다 좋아하는 
본인이 개발한 것들 중에서 학교나 학원에서 해야 했던 과제나 회사에 일로써가 아니라, 개인적으로 개발을 하고 싶어서 만들어본 것들이 있는 팀원을 모십니다. 

• 집요하고 강박적인 
코드에 버그가 있으면, 그 문제를 해결하기 위해서 새벽 4시까지라도 잠을 자지 않고 문제를 찾아내서 스스로 해결해야 하는 성격을 가진 팀원을 모십니다.

• 커뮤니케이션 의지가 있는 
전 세계의 유저들이 실시간으로 사용하는 서비스인 만큼, 고객으로부터 제보되는 다양한 문제 상황이 있습니다. 
이에 대해 파악하고 팀원들과 협력하여, 유저에게 최선의 답을 찾아내기 위해 소통하는 의지가 있는 팀원을 모십니다.

• 문제를 해결하는 데 보람을 느끼는 
개발을 하면서, 어려운 문제를 기술적으로 해결한 경험을 가지고 있고, 그것을 타인에게 잘 설명할 수 있는 팀원을 모십니다.

[에피소든에 지원해야 하는 이유]
• 성공에 대한 확실한 보상 
입사하시게 되면, 본인이 받을 스톡옵션이 회사 성장에 따라 실제로 얼마의 경제적 가치를 가지게 되는지에 대해 명확하게 설명해 드립니다.

• 경제적 자유를 얻을 기회 
글로벌 서비스인만큼 시장에서 평가 받는 회사 가치는 매우 높습니다. 
따라서 팀원이 받게 될 스톡옵션은 유니콘 단계에서도 서울에서 집을 한 채 살 수 있는 것 이상의 보상이 됩니다. 

• 자유로운 의사개진 
Episoden의 경영진은 커뮤니케이션에 대한 책을 집필할 만큼, 대화와 토론을 중요시합니다. 
팀원들의 모든 요구를 들어드리지는 못하지만, 팀원이 면담을 요청하면, 어떻게든 시간을 만들어 서로의 이해를 높이기 위한 커뮤니케이션을 할 의지가 있고, 또 해왔습니다.

• 의미를 느낄 수 있는 일 
Episoden은 경제적인 이유로 영어회화를 마음껏 연습할 수 없었던, 전세계의 수 많은 사람들에게 기회를 제공합니다. 
팀원이 되어 고객들을 만나면, 우리가 사람들에게 무엇을 주고 있는지, 그들의 삶에 얼마나 큰 기여를 하는지 너무 명확하게 느낄 수 있을 것입니다.

• 성장을 주는 도전적인 과업 
전세계 164개국의 사람들을 대상으로, 이전에는 없던 새로운 서비스를 제공하고 있습니다. 
그래서 Episoden팀이 해결해야 할 과제는 무수히 많고, 그 하나 하나가 도전적입니다. 
그 일을 작은 팀이 해야 하기에, 팀원 각자는 도전적인 과업을 부여 받아 주도적으로 일할 수 있게 됩니다.

[주요업무]
• 에피소든 서버 구성 및 개발환경 구축
• 대용랑 Data 관리 및 다양한 서비스 API 개발

[개발환경]
• 주요 기술 : Nestjs, Typescript, TypeOrm,
Socket.io (http://Socket.io)
, WebRTC, Janus, Peerjs, AWS EKS, AWS DocumentDB(MongoDB) AWS Aurora(MySQL), ElasticSearch, Redis, Kafka
• 업무 도구 : Github, WebStrom, IntelliJ, Jira, Confluence, Slack • 웹 어플리케이션 개발, 운영 경력 5년 이상이신 분(또는 그에 준하는 역량을 갖추신 분)
• 인프라 관련 구축 및 운영 경험이 있으신 분
• socket.io를 이용한 서비스 서버 개발 경험이 있으신 분
• Nestjs, Typescript, TypeOrm에 익숙하시고, 그 외 언어(1개 이상)를 습득하신 분
• MongoDB, MySQL, Redis 경험이 있으신 분
• 기본적인 Linux/Unix 명령 사용 능력을 보유하신 분
• 빌드/테스트/배포 자동화를 구축경험이 있으신 분
• GRPC를 이용해 RPC 개발 경험이 있으신 분 (우대)
• AWS EKS, ECS를 이용해 인프라 구축 경험이 있으신 분 (우대) • 내가 개발한 결과에 성취감을 느끼는 사람이면 더 좋습니다.
• 기획, 프론트엔드 개발 구성원들과 문제를 파악하고 해결하는데 적극적인 분이라면 더 좋습니다.
• Docker로 어플리케이션 배포 경험이 있으며 CI/CD 구축/사용경험이 있으신 분이라면 더 좋습니다.
• Microservices 아키텍처 기반의 시스템 개발 경험이 있는 분이라면 더 좋습니다.
• 글로벌, 대용량 트래픽 경험이 있는 분이라면 더 좋습니다.
• ORM 사용과 도메인 모델링 경험이 있는 분이라면 더 좋습니다.
• 동료에게 지식을 공유하고, 피드백을 주는 문화를 좋아하는 분이라면 더 좋습니다.
• JIRA, Confluence, Slack을 활용한 커뮤니케이션에 익숙하신 분이면 더 좋습니다. • 매일 식사 제공 (건강한 생활을 위해, 제대로 된 식사를 제공합니다)
• 직무 및 자기계발 도서/강의 지원
• 업무에 필요한 기기 지원 • 지원 시 GitHub 등의 포트폴리오 첨부
• 서류전형 > 1차 팀워크면접 > 2차기술면접 > 최종합격

* 지원 시 에피소든에 대한 지원 메시지를 꼭 써 주세요. 경력 5~20년 무관 2025-09-07 서울 강남구 선릉로551, 1층 지도보기 · 주소복사 https://jumpit.saramin.co.kr/position/51502192 5.1502192E7 https://jumpit.saramin.co.kr/company/NDgyODcwMjA0NQ==?company_nm=에피소든 1 시니어 백엔드 개발자(5년 이상) 더스윙 💰 취업축하금 50만원 Spring Boot, Spring Data JPA, Java, Kotlin • Kotlin + Spring framework 을 이용한 서비스 API 개발
• Micro Mobility(IoT) Backend Platform 개발

SWING이 사용하는 기술/스택
Spring Boot, JPA,Java, Kotlin • 5년 이상의 Back-end 개발 및 운영 경험, 또는 그에 준하

In [0]:
posting_id_array = pdf['posting_id'].unique()

print("공고 ID 개수: ", len(pdf['posting_id']))
print("공고 ID 개수 (중복제거): ", len(posting_id_array))

공고 ID 개수:  1763
공고 ID 개수 (중복제거):  1288


In [0]:
type(posting_id_array)

numpy.ndarray

In [0]:
display(posting_id_array)

array([51583665., 51502192., 51692814., ..., 51528077., 51593535.,
       51499756.])

## 1) 채용공고 상세페이지 크롤링

### 비밀번호를 시크릿으로 저장 (반드시 먼저)

(권장) Databricks UI → “Security > Secrets” 에서 스코프 생성 (예: saramin)

절대 노트북 코드/깃에 평문으로 남기지 마세요!

### 의존성 (한 번만)

In [0]:
%pip install beautifulsoup4 lxml html5lib requests pytz delta-spark

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 112.2/112.2 kB 3.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 434.2/434.2 MB 1.5 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 203.0/203.0 kB 24.5 MB/s eta 0:00:00
  Created wheel for pyspark: filename=pyspark-4.0.1-py2.py3-none-any.whl size=434813802 sha256=478ad0bf0da5d7fadd3feb348345b4b0da19fb008ac2508db723368fa797b307
  Stored in directory: /root/.cache/pip/wheels/92/31/a4/d5f845fcffd887fee55dd5258b7010c0778e8c75acc81433a5
Successfully built pyspark
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


### 로그인 + 크롤링 + 저장 (업데이트된 전체 코드)

In [0]:
spark = SparkSession.builder.getOrCreate() #SparkSession 생성: Apache Spark 애플리케이션의 진입점(entry point)인 SparkSession 객체를 생성하는 코드
SEOUL = pytz.timezone("Asia/Seoul") # pytz 라이브러리를 사용해 서울 타임존(Asia/Seoul)을 설정

# ---- Secret에서 자격증명 읽기 ----
#usr = dbutils.secrets.get("saramin", "id")   # <- Secret Scope/Key
#pwd = dbutils.secrets.get("saramin", "pw")

usr = "thdsnfla"
pwd = "snflalTHD7!"

# ---- 사이트/헤더 ----
VIEW_URL = "https://www.saramin.co.kr/zf_user/jobs/relay/view?isMypage=no&rec_idx={posting_id}" #채용공고 URL
LOGIN_PAGE = "https://www.saramin.co.kr/zf_user/auth" #로그인 URL
HEADERS = {
    "User-Agent": (
        "Mozilla/5.0 (Windows NT 10.0; Win64; x64) "
        "AppleWebKit/537.36 (KHTML, like Gecko) "
        "Chrome/124.0.0.0 Safari/537.36"
    ),
    "Accept-Language": "ko-KR,ko;q=0.9,en-US;q=0.8,en;q=0.7",
    "Referer": "https://www.saramin.co.kr/",
}

'''
HTTP 헤더 정보: 웹사이트에 요청을 보낼 때 사용하는 HTTP 헤더 정보. 웹사이트가 정상적인 웹 브라우저의 접속으로 인식하게 만들고, 서버로부터 올바른 응답을 받기 위해 필요

"User-Agent": 요청을 보내는 클라이언트(웹 브라우저) 정보를 서버에 알려줌. 여기서는 윈도우 10 운영체제의 크롬 웹 브라우저처럼 보이게 설정

"Accept-Language": 클라이언트가 선호하는 언어를 서버에 알려줌. 한국어(ko-KR)와 영어(en-US)를 선호한다고 설정.

"Referer": 요청이 어느 페이지에서 시작되었는지 알려줌. 이 경우, 사람인 메인 페이지에서 시작된 것처럼 설정.
'''

'\nHTTP 헤더 정보: 웹사이트에 요청을 보낼 때 사용하는 HTTP 헤더 정보. 웹사이트가 정상적인 웹 브라우저의 접속으로 인식하게 만들고, 서버로부터 올바른 응답을 받기 위해 필요\n\n"User-Agent": 요청을 보내는 클라이언트(웹 브라우저) 정보를 서버에 알려줌. 여기서는 윈도우 10 운영체제의 크롬 웹 브라우저처럼 보이게 설정\n\n"Accept-Language": 클라이언트가 선호하는 언어를 서버에 알려줌. 한국어(ko-KR)와 영어(en-US)를 선호한다고 설정.\n\n"Referer": 요청이 어느 페이지에서 시작되었는지 알려줌. 이 경우, 사람인 메인 페이지에서 시작된 것처럼 설정.\n'

In [0]:
# ---- 공통 유틸 ----

#텍스트에서 불필요한 공백을 제거
def clean_text(x: Optional[str]) -> Optional[str]:
    if not x: return None
    t = re.sub(r"\s+", " ", x).strip() #정규 표현식을 사용해 하나 이상의 공백(\s+)을 하나의 공백(" ")으로 대체
    return t if t else None

#문자열에서 숫자만 추출해 정수형으로 변환
def to_int(x: Optional[str]) -> Optional[int]:
    if x is None: return None
    m = re.findall(r"\d+", x.replace(",", ""))
    """
    x.replace(",", ""): 숫자 포맷에 포함될 수 있는 쉼표(,) 먼저 제거
    정규 표현식을 사용해 하나 이상의 연속된 숫자(\d+)를 모두 찾아 리스트로 반환
    """
    return int(m[0]) if m else None #리스트의 첫 번째 항목(m[0])을 정수형으로 변환하여 반환

#문자열에서 비율이나 백분율을 나타내는 부동소수점 숫자를 추출
def to_float_ratio(x: Optional[str]) -> Optional[float]:
    if x is None: return None #입력값 x가 None이면 그대로 None을 반환
    m = re.search(r"(\d+(?:\.\d+)?)\s*%?", x) #문자열 전체에서 패턴에 일치하는 부분을 찾음
    """
    (\d+(?:\.\d+)?):
    
    \d+: 하나 이상의 숫자.
    
    (?:\.\d+)?: (?: ... )는 그룹을 만들지 않는 괄호입니다. ?는 0 또는 1회 반복을 의미하므로, .과 그 뒤의 숫자가 있을 수도 있고 없을 수도 있다는 뜻입니다. 이로 인해 정수(예: "100")와 소수(예: "99.9") 모두를 찾을 수 있습니다.

    \s*%?: 0 또는 1개의 공백(\s)과 0 또는 1개의 퍼센트 기호(%)가 뒤따를 수 있음을 의미합니다.
    """
    return float(m.group(1)) if m else None 
    
    #m.group(1): 첫 번째 그룹(괄호로 묶인 부분)에 해당하는 문자열, 즉 숫자 부분만 추출
    #float(...): 추출한 문자열을 실수(부동소수점)로 변환하여 반환

In [0]:
# ---- 로그인 ----
def create_logged_in_session() -> requests.Session:
    """
    로그인 페이지에서 form/action/토큰을 동적으로 찾고 POST.
    필드명이 바뀌어도 최대한 자동 탐지되도록 구성.
    """
    s = requests.Session() #requests.Session() 객체를 만들어 쿠키, 헤더 등을 자동으로 유지
    s.headers.update(HEADERS)

    # 1) 로그인 페이지 GET (쿠키/토큰 획득)
    r = s.get(LOGIN_PAGE, timeout=15)
    r.raise_for_status()
    soup = BeautifulSoup(r.text, "lxml") #BeautifulSoup을 사용해 HTML을 분석하기 쉬운 객체로 변환하여 파싱

    # 2) 로그인 form/액션/필드명 탐지
    form = soup.find("form") #<form> 태그를 찾음. 이 태그는 로그인 데이터를 보낼 서버 주소를 담고 있음

    # form.get("action")으로 로그인 요청을 보낼 URL을 추출
    if form and form.get("action"): 
        post_url = form.get("action")
        if not post_url.startswith("http"):
            # 상대경로 보정
            #post_url: 이는 로그인 폼의 action 속성에서 추출한 URL입니다. 만약 이 값이 /login_process.do와 같은 상대 경로라면, 웹 크롤링 프로그램은 이 주소가 어디를 가리키는지 알 수 없습니다.
            #requests.compat.urljoin() 함수는 이 문제를 해결해줌. 이 함수는 첫 번째 인자로 주어진 기준 URL과 두 번째 인자로 주어진 상대 URL을 합쳐서 완전한 절대 URL을 만들어줌
            #.compat는 호환성(compatibility)을 위해 사용되는 Python 모듈
            post_url = requests.compat.urljoin(LOGIN_PAGE, post_url)

    else:
        # 액션이 명시되어 있지 않은 경우도 있어 페이지 자체로 POST
        post_url = LOGIN_PAGE
    
    post_url = LOGIN_PAGE
    print(post_url)

    # 이메일/아이디 입력 name 후보
    id_candidates = []
    pw_candidates = []
    csrf_name, csrf_val = None, None

    # input 스캔
    for inp in soup.select("input"): #모든 <input> 태그를 순회

        name = inp.get("name") or ""
        #만약 <input> 태그에 name 속성이 없다면, .get("name")의 결과는 None이 됨. 이 경우, or ""는 None 대신 빈 문자열("")을 반환
        #if inp.get("name") is not None: name = inp.get("name") else: name = "" 을 간결하게 쓴 거
        itype = (inp.get("type") or "").lower()
        #.lower(): 가져온 문자열을 모두 소문자로 변환


        #정규 표현식(re.search)을 이용해 <input> 태그의 name 속성을 분석
        
        # csrf(Cross-Site Request Forgery) 토큰 필드 식별:
        # CSRF 토큰은 보안을 위해 로그인 요청 시 함께 보내야 하는 중요한 값
        if re.search(r"csrf|token", name, re.I):
            csrf_name, csrf_val = name, inp.get("value")
            # r"csrf|token": | (파이프)는 "또는(or)"을 의미. 따라서 "csrf" 또는 "token" 패턴을 찾음.
            #re.I: 대소문자를 구분하지 않고 검색하라는 옵션 (re.IGNORECASE)
            #이 조건이 참이면, 해당 <input> 태그가 CSRF 토큰 필드라고 판단하고, 그 이름(name)과 값(value)을 csrf_name과 csrf_val 변수에 저장

        # id/email 아이디/이메일 입력 필드 식별:
        if itype in ("text","email") or re.search(r"id|email|user", name, re.I):
            id_candidates.append(name)

        # password 비밀번호 입력 필드 식별:
        if itype == "password" or re.search(r"pass", name, re.I):
            pw_candidates.append(name)
    
    print(id_candidates, pw_candidates)

    # 합리적 기본값 = id_candidates[0]
    # 웹사이트의 필드명이 다양하더라도, 가장 일반적인 이름부터 순서대로 확인하여 정확하고 빠르게 올바른 필드명을 찾아내기 위한 전략
    id_field = None
    for cand in ["id","email","login_email","user_id","userEmail"]:
        if cand in id_candidates: 
            id_field = cand # 만약 cand가 id_candidates 리스트에 있다면, 가장 우선순위가 높은(가장 먼저 발견된) 필드명을 id_field 변수에 할당
            break #현재 실행 중인 for 반복문을 즉시 중단
    if not id_field and id_candidates:
        id_field = id_candidates[0]

    pw_field = None
    for cand in ["password","pwd","login_pwd","user_pwd"]:
        if cand in pw_candidates:
            pw_field = cand
            break
    if not pw_field and pw_candidates:
        pw_field = pw_candidates[0]

    if not id_field or not pw_field:
        # 폼 구조가 크게 바뀐 경우: 기본적인 필드명으로 시도
        print("기본적인 필드명을 넣습니다.")
        id_field = id_field or "id"
        pw_field = pw_field or "password"

    
    print(id_field, pw_field)

    payload = {
        id_field: usr,
        pw_field: pwd
    }
    if csrf_name and csrf_val:
        payload[csrf_name] = csrf_val

    # 3) POST 로그인
    r2 = s.post(post_url, data=payload, headers={**HEADERS, "Origin": "https://www.saramin.co.kr"}, timeout=15, allow_redirects=True)
    #requests 라이브러리의 Session 객체(s)를 이용해 로그인 요청을 보냄
    #headers={**HEADERS, "Origin": ...}: 기존 헤더에 Origin 헤더를 추가. Origin은 요청이 시작된 웹사이트를 알려주며, 일부 웹사이트는 보안을 위해 이 헤더를 검사함.

    """
    **HEADERS가 HEADERS 딕셔너리를 풀어헤쳐서 
    {"User-Agent": "...", "Accept-Language": "...", "Referer": "https://www.saramin.co.kr/"}를 생성합니다.

    여기에 {"Origin": "https://www.saramin.co.kr"}라는 새로운 키-값 쌍을 추가합니다.

    결과적으로, headers 변수에는 다음과 같은 새로운 딕셔너리가 할당

    {
    "User-Agent": "...",
    "Accept-Language": "...",
    "Referer": "https://www.saramin.co.kr/",
    "Origin": "https://www.saramin.co.kr",
    }
    """

    """
    Referer와 Origin의 차이점
    두 헤더는 모두 요청의 출처를 나타내지만, 약간 다른 용도로 사용됩니다.

    Referer: 사용자가 현재 페이지로 오기 직전에 방문했던 웹페이지의 주소를 알려줍니다. 예를 들어, Referer가 https://www.saramin.co.kr/라면, 사용자는 사람인 메인 페이지에서 로그인 페이지로 이동했다는 것을 의미합니다.

    Origin: 요청을 보낸 웹페이지의 도메인을 알려줍니다. 이는 주로 CORS(Cross-Origin Resource Sharing)와 같은 보안 메커니즘에서 사용되며, 요청이 어디에서 왔는지 명확하게 식별하는 데 사용됩니다. Referer와 달리 경로 정보는 포함되지 않습니다.

    로그인 요청과 같이 보안이 중요한 상황에서는 웹 서버가 두 헤더를 모두 검증할 수 있기 때문에, 코드는 두 헤더를 모두 포함하여 정상적인 브라우저 요청처럼 보이도록 설계된 것입니다.
    """

    
    # 간단한 성공 휴리스틱: "로그아웃" / 사용자 메뉴 / 마이페이지 등 키워드
    # 로그인 후 받은 응답 페이지(r2.text)의 HTML 내용에 포함되었는지 확인
    ok = any(k in r2.text for k in ["로그아웃", "마이페이지", "회원정보"]) #any(...)는 리스트 안에 있는 키워드 중 단 하나라도 발견되면 True를 반환
    #print(r2.text)
    if not ok:
        # 일부는 리다이렉트 된 HTML에 표시됨 → 한 번 더 검사
        try:
            r3 = s.get("https://www.saramin.co.kr/", timeout=15)
            ok = any(k in r3.text for k in ["로그아웃", "마이페이지", "회원정보"]) # 로그인 후 메인 페이지로 이동했을 때, 로그인 상태가 변경되었을 수 있으므로 메인 페이지에 한 번 더 접속
        except:
            pass
    if not ok:
        raise RuntimeError("Saramin 로그인 실패: 폼/필드명이 변경되었을 수 있습니다. (개발자 콘솔에서 실제 로그인 요청 URL/필드명을 확인해 주세요)")

    return s

# ---- 페이지 로딩 (로그인 세션 사용) ----
def get_soup_with_session(s: requests.Session, url: str, max_retries: int = 3, backoff: float = 1.5) -> Optional[BeautifulSoup]:
    #s: requests.Session: 로그인 정보가 담긴 requests 세션 객체. 이 세션을 통해 로그인 상태를 유지하면서 페이지에 접속함.
    #url: str: 가져올 웹페이지의 URL
    #max_retries: int = 3: 최대 재시도 횟수입니다. 기본값은 3입니다.
    #backoff: float = 1.5: 재시도 간 대기 시간을 기하급수적으로 늘리는 데 사용되는 값

    for attempt in range(1, max_retries + 1):
        try:
            time.sleep(random.uniform(0.6, 1.4))
            resp = s.get(url, timeout=15) #requests 세션을 사용해 URL에 GET 요청을 보내고, 응답을 15초 동안 기다림
            if resp.status_code == 200 and ("jv_header" in resp.text or "wrap_jv_cont" in resp.text):
                #응답 상태 코드가 200(성공)인지 확인
                return BeautifulSoup(resp.text, "lxml")
            time.sleep(backoff ** attempt)
        except requests.RequestException:
            time.sleep(backoff ** attempt)
    return None

-------

### 로그인 함수 테스트

In [0]:
url = "https://www.saramin.co.kr/zf_user/jobs/relay/view?isMypage=no&rec_idx=51606407"
session = create_logged_in_session()
get_soup_with_session(session, url)

https://www.saramin.co.kr/zf_user/auth
['searchword', 'id', 'id_save'] ['password']
id password


---------------------------------------------------------------------------
RuntimeError                              Traceback (most recent call last)
File <command-8079581274090055>, line 2
      1 url = "https://www.saramin.co.kr/zf_user/jobs/relay/view?isMypage=no&rec_idx=51606407"
----> 2 session = create_logged_in_session()
      3 get_soup_with_session(session, url)

File <command-8079581274090051>, line 149, in create_logged_in_session()
    147         pass
    148 if not ok:
--> 149     raise RuntimeError("Saramin 로그인 실패: 폼/필드명이 변경되었을 수 있습니다. (개발자 콘솔에서 실제 로그인 요청 URL/필드명을 확인해 주세요)")
    151 return s

RuntimeError: Saramin 로그인 실패: 폼/필드명이 변경되었을 수 있습니다. (개발자 콘솔에서 실제 로그인 요청 URL/필드명을 확인해 주세요)

In [0]:
LOGIN_URL = "https://www.saramin.co.kr/zf_user/auth/login"
USERNAME = "thdsnfla"
PASSWORD = "snflalTHD7!"

session_test = requests.Session()

login_data = {
    'username': USERNAME,
    'password': PASSWORD
}

response = session_test.post(LOGIN_URL, data=login_data, headers={'User-Agent': 'Mozilla/5.0'})

if response.status_code == 200:
    print("성공")
else:
    print(response.status_code)

성공


In [0]:
import os
import re
import requests
from bs4 import BeautifulSoup
from urllib.parse import urljoin
from requests.adapters import HTTPAdapter, Retry

LOGIN_URL = "https://www.saramin.co.kr/zf_user/auth"

# ★ 하드코딩 금지: 환경변수로 관리
USERNAME = os.getenv("SARAMIN_ID")
PASSWORD = os.getenv("SARAMIN_PW")

session = requests.Session()

# 재시도/백오프 설정 (일시적 연결 종료 대응)
retries = Retry(
    total=5,
    backoff_factor=0.8,
    status_forcelist=[429, 500, 502, 503, 504],
    allowed_methods=["GET", "POST"]
)
session.mount("https://", HTTPAdapter(max_retries=retries))
session.mount("http://", HTTPAdapter(max_retries=retries))

# 일반 브라우저 비슷한 헤더
common_headers = {
    "User-Agent": "Mozilla/5.0",
    "Accept": "text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8",
    "Accept-Language": "ko-KR,ko;q=0.9,en-US;q=0.8,en;q=0.7",
    "Connection": "keep-alive",
}

# 1) 로그인 페이지 GET (쿠키/토큰 확보)
r0 = session.get(LOGIN_URL, headers=common_headers, timeout=(5, 20))
r0.raise_for_status()

soup = BeautifulSoup(r0.text, "html.parser")

# 2) 로그인 form 탐색
#   - 보통 로그인 form은 action과 hidden input(csrf 등)을 가짐
form = None
for f in soup.find_all("form"):
    txt = (f.get("id","") + " " + f.get("name","") + " " + f.get("action","")).lower()
    if "auth" in txt or "login" in txt or "signin" in txt:
        form = f
        break
if form is None and soup.find("form"):
    form = soup.find("form")  # 폼이 하나뿐이면 그걸 사용

if not form:
    raise RuntimeError("로그인 form을 찾지 못했습니다. HTML 구조 변경 가능성.")

action = form.get("action") or LOGIN_URL
action_url = urljoin(r0.url, action)

print("action_url: ", action_url)

# 3) 폼 입력값 구성 (hidden + csrf 포함)
payload = {}
for inp in form.find_all("input"):
    name = inp.get("name")
    if not name:
        continue
    value = inp.get("value", "")
    payload[name] = value

    print(inp, name, value)

# 4) 아이디/비번 필드명 추정 및 주입
#   - 사이트마다 다름: id/userid/login_id/username 중 하나, 비번은 pass/password 등
candidates_id = ["id", "user_id", "userid", "login_id", "username", "loginid"]
candidates_pw = ["pw", "password", "passwd", "user_pw", "login_pw"]

def pick_field(cands, keys):
    keys_lower = [k.lower() for k in keys]
    for c in cands:
        for k in keys_lower:
            if c == k or re.search(rf"\b{re.escape(c)}\b", k):
                return k
    return None

id_key = pick_field(candidates_id, payload.keys()) or "username"
pw_key = pick_field(candidates_pw, payload.keys()) or "password"

print (id_key, pw_key)

payload[id_key] = USERNAME
payload[pw_key] = PASSWORD

# 5) Referer/Content-Type 설정 후 POST
headers_post = {
    **common_headers,
    "Referer": r0.url,
    "Origin": "https://www.saramin.co.kr",
    "Content-Type": "application/x-www-form-urlencoded",
}

r1 = session.post(action_url, data=payload, headers=headers_post,
                  allow_redirects=True, timeout=(5, 30))

# 6) 결과 판정
#   - 보통 로그인 성공 시 마이페이지 등으로 리디렉트, 실패 시 같은 페이지 + 에러메시지

ok = False
if r1.status_code in (200, 302):
    # 로그인 여부를 쿠키/본문으로 추정 (사이트마다 다름)
    # 예: "로그아웃", "마이페이지" 같은 키워드가 있으면 성공으로 가정
    if ("로그아웃" in r1.text) or ("마이페이지" in r1.text) or ("logout" in r1.text.lower()):
        ok = True

print("r1.text: ", r1.text)

print("로그인 성공" if ok else f"로그인 실패 (status={r1.status_code}, url={r1.url})")
# 디버깅용: 실패 시 일부 힌트 출력
if not ok:
    print("응답 길이:", len(r1.text))
    print("히스토리:", [f.status_code for f in r1.history])


action_url:  https://www.saramin.co.kr/zf_user/auth/login
<input name="m_code" type="hidden" value="0"/> m_code 0
<input name="page_url" type="hidden" value=""/> page_url 
<input name="url" type="hidden" value=""/> url 
<input name="FrameKey" type="hidden" value=""/> FrameKey 
<input name="ig_value" type="hidden" value=""/> ig_value 
<input name="subRef" type="hidden" value="saramin"/> subRef saramin
<input id="login_tab" name="login_tab" type="hidden" value="p"/> login_tab p
<input class="txt_tool" id="id" name="id" required="" type="text" value=""/> id 
<input class="txt_tool" id="password" maxlength="32" name="password" required="" type="password" value=""/> password 
<input id="autologin" name="autologin" onmousedown="try{n_trackEvent('login', 'pc_login_page' , 'login_save', '');}catch(e){}" type="checkbox"/> autologin 
<input id="id_save" name="id_save" onmousedown="try{n_trackEvent('login', 'pc_login_page' , 'id_save', '');}catch(e){}" type="checkbox"/> id_save 
id password
r1.te

In [0]:
import requests
from bs4 import BeautifulSoup
from urllib.parse import urljoin
from requests.adapters import HTTPAdapter, Retry

LOGIN_URL = "https://www.saramin.co.kr/zf_user/auth"
ID = "thdsnfla"          # ★ 대화에 노출된 비번은 즉시 변경하세요
PW = "snflalTHD7!"       # ★ 비번 교체 필수

session = requests.Session()

# 재시도(일시적 끊김 대응)
retries = Retry(total=5, backoff_factor=0.8,
                status_forcelist=[429,500,502,503,504],
                allowed_methods=["GET","POST"])
session.mount("https://", HTTPAdapter(max_retries=retries))
session.mount("http://", HTTPAdapter(max_retries=retries))

headers = {
    "User-Agent": "Mozilla/5.0",
    "Accept": "text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8",
    "Accept-Language": "ko-KR,ko;q=0.9,en-US;q=0.8",
    "Connection": "keep-alive",
}

# 1) 로그인 페이지 먼저 GET (쿠키/히든/토큰 확보)
r0 = session.get(LOGIN_URL, headers=headers, timeout=(5,20))
r0.raise_for_status()
soup = BeautifulSoup(r0.text, "html.parser")

# 2) form 추출 (action과 hidden input들 포함)
form = None
for f in soup.find_all("form"):
    text = (f.get("id","") + " " + f.get("name","") + " " + f.get("action","")).lower()
    if "auth" in text or "login" in text:
        form = f
        break
if form is None:
    form = soup.find("form")  # 폼이 하나면 그걸 사용

action = form.get("action") or LOGIN_URL
post_url = urljoin(r0.url, action)

# 3) payload 구성 (모든 hidden 포함)
payload = {}
for inp in form.find_all("input"):
    name = inp.get("name")
    if not name:
        continue
    payload[name] = inp.get("value", "")

# 4) 실제 필드명 맞추기: id / password
payload["id"] = ID
payload["password"] = PW

# (탭/회원구분 등 필요한 값 세팅이 필요할 수도 있음)
# 예: payload.setdefault("login_tab_default", "p")  # 개인 탭
#     payload.setdefault("ig_value", "")            # 페이지 상황 따라 다름

headers_post = {
    **headers,
    "Referer": r0.url,
    "Origin": "https://www.saramin.co.kr",
    "Content-Type": "application/x-www-form-urlencoded",
}

# 5) POST (리다이렉트 허용)
r1 = session.post(post_url, data=payload, headers=headers_post,
                  allow_redirects=True, timeout=(5,30))

# 6) 성공 판정 (사이트 문구 기반 커스터마이즈)
ok = ("로그아웃" in r1.text) or ("마이페이지" in r1.text) or ("logout" in r1.text.lower())
print("로그인 성공" if ok else f"로그인 실패 (status={r1.status_code}, url={r1.url})")

print(r1.text)

로그인 성공
<!DOCTYPE html><html lang="ko">
<head>
        <title>사람인</title>    <meta http-equiv="X-UA-Compatible" content="IE=Edge" >
<meta http-equiv="Content-Type" content="text/html; charset=utf-8" >
<meta http-equiv="Content-Language" content="ko-KR" >
<meta name="naver-site-verification" content="86455485e27cab6986d130e4c3b90c5b516820d1" >
<meta name="naver" content="nosublinks" >    <meta property="og:title" content="사람인" >
<meta property="og:image" content="//www.saraminimage.co.kr/logo/saraminsnslogo.png" >
<meta property="og:site_name" content="사람인" >
<meta property="og:type" content="website" >
<meta property="og:locale" content="ko_KR" >
<meta property="fb:app_id" content="1593727887570039" >
<meta property="og:image:width" content="200" >
<meta property="og:image:height" content="200" >    <link href="/sri_css/layout.css?v=20250909103156" media="all" rel="stylesheet" type="text/css" >
<link href="/sri_css/pattern.css?v=20250909103156" media="all" rel="stylesheet" type="text/cs

In [0]:
import os
import time
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException, NoSuchElementException, UnexpectedAlertPresentException

ID = "thdsnfla"          # ★ 대화에 노출된 비번은 즉시 변경하세요
PW = "snflalTHD7!"       # ★ 비번 교체 필수
#assert ID and PW, "환경변수 SARAMIN_ID / SARAMIN_PW 를 설정하세요."

LOGIN_URL = "https://www.saramin.co.kr/zf_user/auth"

def close_any_alert(driver, timeout=2):
    try:
        WebDriverWait(driver, timeout).until(EC.alert_is_present())
        driver.switch_to.alert.accept()
        time.sleep(0.3)
    except TimeoutException:
        pass

def first_displayed(els):
    for e in els:
        try:
            if e.is_displayed():
                return e
        except Exception:
            continue
    return None

def find_login_context(driver, wait):
    """
    로그인 입력 컨텍스트(폼/레이어)와 제출 버튼을 찾아서 반환.
    반환: (form_element, id_input, pw_input, submit_button)
    """
    # 1) 모달(레이어) 먼저 탐색: #pop_login_layer 내부의 form
    try:
        layer = driver.find_element(By.ID, "pop_login_layer")
        if layer.is_displayed():
            # 레이어 내부 visible input
            id_candidates = layer.find_elements(By.CSS_SELECTOR, 'input[name="id"], #ly_id')
            pw_candidates = layer.find_elements(By.CSS_SELECTOR, 'input[name="password"], #ly_password')
            id_input = first_displayed(id_candidates)
            pw_input = first_displayed(pw_candidates)
            if id_input and pw_input:
                # 제출 버튼은 동일 레이어 폼 안의 .btn_login
                submit_btns = layer.find_elements(By.CSS_SELECTOR, "button.btn_login, button[type='submit']")
                submit_btn = first_displayed(submit_btns)
                if submit_btn:
                    # form은 상위 form으로
                    form = id_input.find_element(By.XPATH, "./ancestor::form")
                    return form, id_input, pw_input, submit_btn
    except NoSuchElementException:
        pass

    # 2) 페이지형 로그인 폼 (auth 페이지)
    # visible인 id/password 인풋을 가진 form과 .btn_login 찾기
    id_candidates = driver.find_elements(By.CSS_SELECTOR, 'form input[name="id"], form #ly_id')
    pw_candidates = driver.find_elements(By.CSS_SELECTOR, 'form input[name="password"], form #ly_password')
    id_input = first_displayed(id_candidates)
    pw_input = first_displayed(pw_candidates)
    if id_input and pw_input:
        try:
            form = id_input.find_element(By.XPATH, "./ancestor::form")
            # form 내 제출 버튼
            submit_btns = form.find_elements(By.CSS_SELECTOR, "button.btn_login, button[type='submit']")
            submit_btn = first_displayed(submit_btns)
            if submit_btn:
                return form, id_input, pw_input, submit_btn
        except NoSuchElementException:
            pass

    # 3) 아직 컨텍스트가 없다면 헤더의 로그인 버튼 클릭해서 레이어 띄우기
    try:
        signin_btn = driver.find_element(By.CSS_SELECTOR, "a.btn_sign.signin[href*='/zf_user/auth']")
        if signin_btn.is_displayed():
            signin_btn.click()
            time.sleep(0.3)
            close_any_alert(driver)
            # 레이어 다시 시도
            layer = WebDriverWait(driver, 5).until(
                EC.visibility_of_element_located((By.ID, "pop_login_layer"))
            )
            id_input = first_displayed(layer.find_elements(By.CSS_SELECTOR, 'input[name="id"], #ly_id'))
            pw_input = first_displayed(layer.find_elements(By.CSS_SELECTOR, 'input[name="password"], #ly_password'))
            submit_btn = first_displayed(layer.find_elements(By.CSS_SELECTOR, "button.btn_login, button[type='submit']"))
            if id_input and pw_input and submit_btn:
                form = id_input.find_element(By.XPATH, "./ancestor::form")
                return form, id_input, pw_input, submit_btn
    except Exception:
        pass

    return None, None, None, None

def logged_in(driver):
    html = driver.page_source
    # 1) 로그아웃 텍스트나 링크 존재
    if "로그아웃" in html or "logout" in html.lower():
        return True
    # 2) 헤더 로그인 버튼이 사라졌는지 체크
    try:
        driver.find_element(By.CSS_SELECTOR, "a.btn_sign.signin")
        # 여전히 보이면 미로그인
        return False
    except NoSuchElementException:
        # 없으면 로그인됐을 가능성 큼
        return True

def main(headless=False):
    chrome_opts = Options()
    if headless:
        chrome_opts.add_argument("--headless=new")
    chrome_opts.add_argument("--lang=ko-KR")
    chrome_opts.add_argument("--window-size=1280,900")
    chrome_opts.add_argument("--disable-blink-features=AutomationControlled")
    chrome_opts.add_argument("--no-sandbox")
    chrome_opts.add_argument("--disable-dev-shm-usage")
    # (선택) UA 지정
    chrome_opts.add_argument(
        "--user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) "
        "AppleWebKit/537.36 (KHTML, like Gecko) Chrome/126.0.0.0 Safari/537.36"
    )

    driver = webdriver.Chrome(options=chrome_opts)
    wait = WebDriverWait(driver, 15)

    try:
        driver.get(LOGIN_URL)
        close_any_alert(driver)

        form, id_input, pw_input, submit_btn = find_login_context(driver, wait)
        if not all([form, id_input, pw_input, submit_btn]):
            raise RuntimeError("로그인 입력 폼/레이어를 찾지 못했습니다. DOM이 변경되었을 수 있어요.")

        # 탭이 필요한 경우(개인/기업) 기본은 개인: hidden input들로 제어될 수 있으나, 필드만 채우면 서버가 인식하는 구조.
        id_input.clear()
        id_input.send_keys(ID)
        time.sleep(0.2)
        pw_input.clear()
        pw_input.send_keys(PW)
        time.sleep(0.2)

        submit_btn.click()
        close_any_alert(driver)

        # 리다이렉트/렌더 대기
        time.sleep(1.0)
        # 최대 15초 동안 로그인 성공 신호 대기
        WebDriverWait(driver, 15).until(lambda d: logged_in(d))

        print("✅ 로그인 성공")
        # 필요시 쿠키 사용
        cookies = {c["name"]: c["value"] for c in driver.get_cookies()}
        print("세션 쿠키 예:", list(cookies.keys())[:5])

    except UnexpectedAlertPresentException:
        try:
            driver.switch_to.alert.accept()
        except Exception:
            pass
        raise
    except Exception as e:
        # 디버깅 편의: 현재 페이지 저장
        try:
            with open("saramin_login_debug.html", "w", encoding="utf-8") as f:
                f.write(driver.page_source)
            print("❌ 로그인 실패. 'saramin_login_debug.html' 로 페이지 소스를 저장했습니다.")
        except Exception:
            pass
        raise e
    finally:
        # driver.quit()  # 디버깅 중이면 주석 처리
        pass

if __name__ == "__main__":
    main(headless=False)  # 무인화 시 True


---------------------------------------------------------------------------
SessionNotCreatedException                Traceback (most recent call last)
File <command-5099870694463344>, line 178
    175         pass
    177 if __name__ == "__main__":
--> 178     main(headless=False)

File <command-5099870694463344>, line 126, in main(headless)
    120 # (선택) UA 지정
    121 chrome_opts.add_argument(
    122     "--user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) "
    123     "AppleWebKit/537.36 (KHTML, like Gecko) Chrome/126.0.0.0 Safari/537.36"
    124 )
--> 126 driver = webdriver.Chrome(options=chrome_opts)
    127 wait = WebDriverWait(driver, 15)
    129 try:

File /local_disk0/.ephemeral_nfs/envs/pythonEnv-38ac9a25-0971-4705-99b7-fadf15b3d032/lib/python3.10/site-packages/selenium/webdriver/chrome/webdriver.py:45, in WebDriver.__init__(self, options, service, keep_alive)
     42 service = service if service else Service()
     43 options = options if options else Options()
---> 45

같은 노트북/클러스터에서 동시에 Selenium 세션 2개 이상 띄우지 않기

좀비 Chrome/Chromedriver가 남아있으면 종료

매 실행마다 고유한 user-data-dir를 지정 (혹은 아예 지정하지 않기)

Databricks처럼 환경에서 기본적으로 --user-data-dir이 강제로 붙는 경우 → 내가 직접 유니크 경로 지정

In [0]:
import os, tempfile, shutil, time
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

def make_chrome(headless=False):
    # 1) 실행마다 고유한 프로필 폴더 생성
    user_data_dir = tempfile.mkdtemp(prefix="selenium_chrome_profile_")

    chrome_opts = Options()
    if headless:
        chrome_opts.add_argument("--headless=new")

    chrome_opts.add_argument("--lang=ko-KR")
    chrome_opts.add_argument("--window-size=1280,900")
    chrome_opts.add_argument("--disable-dev-shm-usage")
    chrome_opts.add_argument("--no-sandbox")

    # 2) 고유 프로필 사용 (중복 충돌 예방)
    chrome_opts.add_argument(f"--user-data-dir={user_data_dir}")
    # (선택) 프로필 하위 디렉터리도 고유하게
    chrome_opts.add_argument("--profile-directory=Default")

    # (선택) 첫 실행 마법사/팝업 방지
    chrome_opts.add_argument("--no-first-run")
    chrome_opts.add_argument("--no-default-browser-check")
    # (선택) 자동화 티 약화
    chrome_opts.add_experimental_option("excludeSwitches", ["enable-automation"])
    chrome_opts.add_experimental_option("useAutomationExtension", False)

    driver = webdriver.Chrome(options=chrome_opts)

    # driver와 프로필 경로를 함께 반환해서 마지막에 정리
    return driver, user_data_dir

def cleanup(driver, user_data_dir):
    try:
        driver.quit()
    finally:
        # 3) 프로필 폴더 정리 (잠시 대기 후 삭제: 파일 핸들 해제 대기)
        for _ in range(3):
            try:
                shutil.rmtree(user_data_dir, ignore_errors=True)
                break
            except Exception:
                time.sleep(0.5)

# 사용 예시
driver, profile_dir = make_chrome(headless=False)
try:
    driver.get("https://www.saramin.co.kr/zf_user/auth")
    WebDriverWait(driver, 15).until(EC.title_contains("사람인"))
    # ... 로그인 자동화 로직 ...
finally:
    cleanup(driver, profile_dir)


---------------------------------------------------------------------------
SessionNotCreatedException                Traceback (most recent call last)
File <command-5099870694463346>, line 51
     48                 time.sleep(0.5)
     50 # 사용 예시
---> 51 driver, profile_dir = make_chrome(headless=False)
     52 try:
     53     driver.get("https://www.saramin.co.kr/zf_user/auth")

File <command-5099870694463346>, line 33, in make_chrome(headless)
     30 chrome_opts.add_experimental_option("excludeSwitches", ["enable-automation"])
     31 chrome_opts.add_experimental_option("useAutomationExtension", False)
---> 33 driver = webdriver.Chrome(options=chrome_opts)
     35 # driver와 프로필 경로를 함께 반환해서 마지막에 정리
     36 return driver, user_data_dir

File /local_disk0/.ephemeral_nfs/envs/pythonEnv-38ac9a25-0971-4705-99b7-fadf15b3d032/lib/python3.10/site-packages/selenium/webdriver/chrome/webdriver.py:45, in WebDriver.__init__(self, options, service, keep_alive)
     42 service = service if servi

In [0]:
import os, tempfile, shutil, time
from selenium import webdriver
from selenium.webdriver.chrome.options import Options

def make_driver(headless=False):
    # 실행마다 유니크한 프로필 디렉터리 생성
    user_data_dir = tempfile.mkdtemp(prefix="selenium_chrome_profile_")

    chrome_opts = Options()
    if headless:
        chrome_opts.add_argument("--headless=new")
    chrome_opts.add_argument("--lang=ko-KR")
    chrome_opts.add_argument("--window-size=1280,900")
    chrome_opts.add_argument("--disable-dev-shm-usage")
    chrome_opts.add_argument("--no-sandbox")

    # ★ 충돌 방지 핵심
    chrome_opts.add_argument(f"--user-data-dir={user_data_dir}")
    chrome_opts.add_argument("--profile-directory=Default")
    chrome_opts.add_argument("--no-first-run")
    chrome_opts.add_argument("--no-default-browser-check")
    chrome_opts.add_experimental_option("excludeSwitches", ["enable-automation"])
    chrome_opts.add_experimental_option("useAutomationExtension", False)

    # (선택) 디버깅 포트도 유니크하게
    chrome_opts.add_argument(f"--remote-debugging-port={9222 + os.getpid()%2000}")

    driver = webdriver.Chrome(options=chrome_opts)
    return driver, user_data_dir

def cleanup(driver, user_data_dir):
    try:
        driver.quit()
    finally:
        # 잠시 대기 후 프로필 폴더 삭제(락 해제 대기)
        for _ in range(5):
            try:
                shutil.rmtree(user_data_dir, ignore_errors=True)
                break
            except Exception:
                time.sleep(0.5)

# 사용 예
driver, profile_dir = make_driver(headless=False)
try:
    driver.get("https://www.google.com/")
    # ... 작업 ...
finally:
    cleanup(driver, profile_dir)


---------------------------------------------------------------------------
ModuleNotFoundError                       Traceback (most recent call last)
File <command-5099870694463347>, line 2
      1 import os, tempfile, shutil, time
----> 2 from selenium import webdriver
      3 from selenium.webdriver.chrome.options import Options
      5 def make_driver(headless=False):
      6     # 실행마다 유니크한 프로필 디렉터리 생성

ModuleNotFoundError: No module named 'selenium'

-------

In [0]:
# ---- 파싱: (이전 답변의 파서 그대로 재사용) ----
def parse_summary_keyvalue(soup: BeautifulSoup) -> Dict[str, str]:
    out = {}
    for dl in soup.select(".jv_summary .cont .col dl"):
        dt = clean_text(dl.select_one("dt").get_text(strip=True)) if dl.select_one("dt") else None
        dd = clean_text(dl.select_one("dd").get_text(" ", strip=True)) if dl.select_one("dd") else None
        if dt and dd:
            out[dt] = dd
    return out

def find_text_after_label(soup: BeautifulSoup, label: str) -> Optional[str]:
    label_nodes = soup.find_all(lambda tag: tag.name in ["dt","th","span","div","strong"] and label in tag.get_text())
    for node in label_nodes:
        sib = node.find_next_sibling(["dd","td","span","div"])
        if sib:
            t = clean_text(sib.get_text(" ", strip=True))
            if t:
                return t
    return None

def section_box_by_title(soup: BeautifulSoup, title_ko: str) -> Optional[BeautifulSoup]:
    h2 = soup.find(lambda tag: tag.name in ["h2","h3","div","strong"] and title_ko in tag.get_text())
    if not h2:
        for jv in soup.select(".jv_cont"):
            if title_ko in jv.get_text():
                return jv
        return None
    for parent in h2.parents:
        if getattr(parent, "get", None) and "jv_cont" in parent.get("class", []):
            return parent
    return h2.find_parent() or h2

def parse_start_end_datetime(soup: BeautifulSoup):
    sec = section_box_by_title(soup, "접수기간 및 방법")
    if not sec: return None, None
    start_dd = end_dd = None
    for dl in sec.select("dl.info_period"):
        for dt, dd in zip(dl.select("dt"), dl.select("dd")):
            key = clean_text(dt.get_text(" ", strip=True))
            val = clean_text(dd.get_text(" ", strip=True))
            if key == "시작일": start_dd = val
            elif "마감일" in key: end_dd = val
    return start_dd, end_dd

def parse_is_closed(soup: BeautifulSoup) -> Optional[bool]:
    btn_apply = soup.select_one(".btn_apply .sri_btn_immediately, .jv_howto .sri_btn_immediately")
    dday = soup.select_one(".btn_apply .dday, .recruit_func .num_dday")
    if dday and "마감" in dday.get_text(): return True
    return False if btn_apply else None

def parse_meta_counts(soup: BeautifulSoup) -> Dict[str, Optional[int]]:
    views = bookmarks = homepage = None
    for li in soup.select(".jv_summary .list_meta li"):
        t = li.get_text(" ", strip=True)
        if "조회수" in t: views = to_int(t)
    scrap_btn = soup.select_one(".btn_scrap .txt_scrap")
    if scrap_btn: bookmarks = to_int(scrap_btn.get_text())
    return {"posting_views_total": views, "posting_bookmarks_total": bookmarks, "homepage_visits_total": homepage}

def pick_by_label_in_stats_box(box: BeautifulSoup, label_text: str) -> Dict[str, Optional[Any]]:
    out = {}
    title_node = box.find(lambda tag: tag.name in ["strong","h3","h4","div"] and label_text in tag.get_text())
    if not title_node: return out
    container = title_node.find_parent("div", class_="box_chart") or title_node.parent
    total_node = container.select_one(".total span, .total .value, .total")
    total = to_int(total_node.get_text()) if total_node else None

    for dl in container.select(".legend dl"):
        legend = clean_text(dl.select_one("dt").get_text(" ", strip=True)) if dl.select_one("dt") else None
        val_num_el = dl.select_one(".value, .perc, dd")
        val_num = to_int(val_num_el.get_text(" ", strip=True)) if val_num_el else None
        perc_el = dl.select_one(".perc")
        perc = to_float_ratio(perc_el.get_text(" ", strip=True)) if perc_el else None
        if legend: out[legend] = {"value": val_num, "perc": perc}
    for col in container.select(".chart_line .col"):
        legend = clean_text(col.select_one(".legend").get_text(" ", strip=True)) if col.select_one(".legend") else None
        val_node = col.select_one(".value")
        val_num = to_int(val_node.get_text()) if val_node else None
        if legend: out[legend] = {"value": val_num, "perc": None}
    out_norm = {}
    for k, v in out.items():
        key = re.sub(r"\s+", " ", k.replace("<br>", " ").replace("\n", " ")).strip()
        out_norm[key] = v
    return {"_total": total, **out_norm}

def parse_applicant_stats(soup: BeautifulSoup) -> Dict[str, Optional[int]]:
    result = {k: None for k in [
        "applicants_total",
        "applicants_by_exp_new","applicants_by_exp_less_than_1yr","applicants_by_exp_1_3yrs","applicants_by_exp_3_5yrs","applicants_by_exp_over_5yrs",
        "applicants_by_salary_2200_2600","applicants_by_salary_2600_3000","applicants_by_salary_3000_4000","applicants_by_salary_over_4000",
        "applicants_by_gender_total","applicants_by_gender_male","applicants_by_gender_female","applicants_by_gender_ratio_male","applicants_by_gender_ratio_female",
        "applicants_by_age_20s","applicants_by_age_30s","applicants_by_age_40s","applicants_by_age_50s","applicants_by_age_over_60s",
        "applicants_by_education_highschool_or_less","applicants_by_education_associates","applicants_by_education_bachelors","applicants_by_education_masters","applicants_by_education_phd",
        "applicants_submitted_portfolio",
    ]}
    sec = section_box_by_title(soup, "지원자 통계")
    if not sec: return result

    total_box = sec.select_one(".box_chart .total span, .box_chart .total .value")
    total = to_int(total_box.get_text()) if total_box else None
    result["applicants_total"] = total
    result["applicants_by_gender_total"] = total

    gender = pick_by_label_in_stats_box(sec, "성별")
    if gender:
        result["applicants_by_gender_male"] = (gender.get("남자") or {}).get("value")
        result["applicants_by_gender_female"] = (gender.get("여자") or {}).get("value")
        result["applicants_by_gender_ratio_male"] = (gender.get("남자") or {}).get("perc")
        result["applicants_by_gender_ratio_female"] = (gender.get("여자") or {}).get("perc")

    age = pick_by_label_in_stats_box(sec, "연령")
    if age:
        result["applicants_by_age_20s"] = (age.get("20대") or {}).get("value")
        result["applicants_by_age_30s"] = (age.get("30대") or {}).get("value")
        result["applicants_by_age_40s"] = (age.get("40대") or {}).get("value")
        result["applicants_by_age_50s"] = (age.get("50대") or {}).get("value")
        result["applicants_by_age_over_60s"] = (age.get("60대 이상") or {}).get("value")

    edu = pick_by_label_in_stats_box(sec, "학력")
    if edu:
        result["applicants_by_education_highschool_or_less"] = (edu.get("고졸이하") or {}).get("value")
        result["applicants_by_education_associates"] = (edu.get("2~3년제") or {}).get("value")
        result["applicants_by_education_bachelors"] = (edu.get("4년제") or {}).get("value")
        result["applicants_by_education_masters"] = (edu.get("석사") or {}).get("value")
        result["applicants_by_education_phd"] = (edu.get("박사") or {}).get("value")

    exp = pick_by_label_in_stats_box(sec, "경력")
    if exp:
        result["applicants_by_exp_new"] = (exp.get("신입") or {}).get("value")
        result["applicants_by_exp_less_than_1yr"] = (exp.get("1년 미만") or {}).get("value")
        result["applicants_by_exp_1_3yrs"] = (exp.get("1~3년") or {}).get("value")
        result["applicants_by_exp_3_5yrs"] = (exp.get("3~5년") or {}).get("value")
        result["applicants_by_exp_over_5yrs"] = (exp.get("5년 이상") or {}).get("value")

    sal = pick_by_label_in_stats_box(sec, "연봉")
    if sal:
        k_2200_2600 = next((k for k in sal if "2,200" in k and "2,600" in k), None)
        k_2600_3000 = next((k for k in sal if "2,600" in k and "3,000" in k), None)
        k_3000_4000 = next((k for k in sal if "3,000" in k and "4,000" in k), None)
        k_over_4000 = next((k for k in sal if ("4,000" in k and "이상" in k) or ("4000" in k and "이상" in k)), None)
        result["applicants_by_salary_2200_2600"] = (sal.get(k_2200_2600) or {}).get("value") if k_2200_2600 else None
        result["applicants_by_salary_2600_3000"] = (sal.get(k_2600_3000) or {}).get("value") if k_2600_3000 else None
        result["applicants_by_salary_3000_4000"] = (sal.get(k_3000_4000) or {}).get("value") if k_3000_4000 else None
        result["applicants_by_salary_over_4000"] = (sal.get(k_over_4000) or {}).get("value") if k_over_4000 else None

    # 포트폴리오 제출 추정
    node = sec.select_one(".portfolio .legend .ptf .perc span")
    result["applicants_submitted_portfolio"] = to_int(node.get_text()) if node else None
    return result

def parse_application_method_and_format(soup: BeautifulSoup):
    sec = section_box_by_title(soup, "접수기간 및 방법")
    if not sec: return None, None
    method_texts = {clean_text(b.get_text(" ", strip=True)) for b in sec.select(".guide .method .sri_btn_1, .guide .method button, .guide .method a") if clean_text(b.get_text(" ", strip=True))}
    method = ", ".join(sorted(method_texts)) if method_texts else None
    tt = sec.select_one(".guide .template .toolTipCont")
    fmt = clean_text(tt.get_text(" ", strip=True)) if tt else find_text_after_label(sec, "제출서류")
    return method, fmt

def parse_record(soup: BeautifulSoup, posting_id: int) -> Dict[str, Any]:
    title = clean_text(soup.select_one(".jv_header h1.tit_job").get_text(" ", strip=True)) if soup.select_one(".jv_header h1.tit_job") else None
    company = clean_text(soup.select_one(".jv_header .company").get_text(" ", strip=True)) if soup.select_one(".jv_header .company") else None

    summary = parse_summary_keyvalue(soup)
    experience = summary.get("경력")
    education = summary.get("학력")
    employment_type = summary.get("근무형태")
    salary = summary.get("급여")
    work_location = summary.get("근무지역")

    working_hours = find_text_after_label(soup, "근무시간")
    position = find_text_after_label(soup, "모집분야") or find_text_after_label(soup, "직무")

    start_dt, end_dt = parse_start_end_datetime(soup)
    meta = parse_meta_counts(soup)
    stats = parse_applicant_stats(soup)
    app_method, app_format = parse_application_method_and_format(soup)
    is_closed = parse_is_closed(soup)

    collected_at = datetime.now(SEOUL).strftime("%Y-%m-%d %H:%M:%S")

    return {
        "posting_title": title,
        "company_name": company,
        "posting_id": int(posting_id),
        "is_closed": bool(is_closed) if is_closed is not None else None,
        "posting_bookmarks_total": meta.get("posting_bookmarks_total"),
        "posting_views_total": meta.get("posting_views_total"),
        "homepage_visits_total": meta.get("homepage_visits_total"),
        "experience": experience,
        "education": education,
        "employment_type": employment_type,
        "salary": salary,
        "position": position,
        "working_hours": working_hours,
        "work_location": work_location,
        "start_datetime": start_dt,
        "end_datetime": end_dt,
        "application_method": app_method,
        "application_format": app_format,
        "applicants_total": stats["applicants_total"],
        "applicants_by_exp_new": stats["applicants_by_exp_new"],
        "applicants_by_exp_less_than_1yr": stats["applicants_by_exp_less_than_1yr"],
        "applicants_by_exp_1_3yrs": stats["applicants_by_exp_1_3yrs"],
        "applicants_by_exp_3_5yrs": stats["applicants_by_exp_3_5yrs"],
        "applicants_by_exp_over_5yrs": stats["applicants_by_exp_over_5yrs"],
        "applicants_by_salary_2200_2600": stats["applicants_by_salary_2200_2600"],
        "applicants_by_salary_2600_3000": stats["applicants_by_salary_2600_3000"],
        "applicants_by_salary_3000_4000": stats["applicants_by_salary_3000_4000"],
        "applicants_by_salary_over_4000": stats["applicants_by_salary_over_4000"],
        "applicants_by_gender_total": stats["applicants_by_gender_total"],
        "applicants_by_gender_male": stats["applicants_by_gender_male"],
        "applicants_by_gender_female": stats["applicants_by_gender_female"],
        "applicants_by_gender_ratio_male": stats["applicants_by_gender_ratio_male"],
        "applicants_by_gender_ratio_female": stats["applicants_by_gender_ratio_female"],
        "applicants_by_age_20s": stats["applicants_by_age_20s"],
        "applicants_by_age_30s": stats["applicants_by_age_30s"],
        "applicants_by_age_40s": stats["applicants_by_age_40s"],
        "applicants_by_age_50s": stats["applicants_by_age_50s"],
        "applicants_by_age_over_60s": stats["applicants_by_age_over_60s"],
        "applicants_by_education_highschool_or_less": stats["applicants_by_education_highschool_or_less"],
        "applicants_by_education_associates": stats["applicants_by_education_associates"],
        "applicants_by_education_bachelors": stats["applicants_by_education_bachelors"],
        "applicants_by_education_masters": stats["applicants_by_education_masters"],
        "applicants_by_education_phd": stats["applicants_by_education_phd"],
        "applicants_submitted_portfolio": stats["applicants_submitted_portfolio"],
        "saramin_posting_details_collection_time": collected_at
    }

# ---- 메인 실행 ----
def crawl_with_login(posting_ids: np.ndarray) -> pd.DataFrame:
    session = create_logged_in_session()
    rows = []
    for pid in posting_ids:
        url = VIEW_URL.format(posting_id=int(pid))
        soup = get_soup_with_session(session, url)
        if not soup:
            # 실패해도 기록 남김
            rows.append({"posting_title": None, "company_name": None, "posting_id": int(pid),
                         "is_closed": None, "posting_bookmarks_total": None, "posting_views_total": None, "homepage_visits_total": None,
                         "experience": None, "education": None, "employment_type": None, "salary": None, "position": None,
                         "working_hours": None, "work_location": None, "start_datetime": None, "end_datetime": None,
                         "application_method": None, "application_format": None,
                         "applicants_total": None, "applicants_by_exp_new": None, "applicants_by_exp_less_than_1yr": None,
                         "applicants_by_exp_1_3yrs": None, "applicants_by_exp_3_5yrs": None, "applicants_by_exp_over_5yrs": None,
                         "applicants_by_salary_2200_2600": None, "applicants_by_salary_2600_3000": None, "applicants_by_salary_3000_4000": None,
                         "applicants_by_salary_over_4000": None, "applicants_by_gender_total": None, "applicants_by_gender_male": None,
                         "applicants_by_gender_female": None, "applicants_by_gender_ratio_male": None, "applicants_by_gender_ratio_female": None,
                         "applicants_by_age_20s": None, "applicants_by_age_30s": None, "applicants_by_age_40s": None,
                         "applicants_by_age_50s": None, "applicants_by_age_over_60s": None,
                         "applicants_by_education_highschool_or_less": None, "applicants_by_education_associates": None,
                         "applicants_by_education_bachelors": None, "applicants_by_education_masters": None,
                         "applicants_by_education_phd": None, "applicants_submitted_portfolio": None,
                         "saramin_posting_details_collection_time": datetime.now(SEOUL).strftime("%Y-%m-%d %H:%M:%S")})
            continue
        rows.append(parse_record(soup, int(pid)))
    return pd.DataFrame(rows)

# ----- 입력 배열 준비 (이미 보유했다고 가정)
# posting_id_array = np.array([51606407, 51687390, ...])

# ----- 실행
df_pd = crawl_with_login(posting_id_array)

# 스키마/컬럼 순서 고정
cols = [
    "posting_title","company_name","posting_id","is_closed",
    "posting_bookmarks_total","posting_views_total","homepage_visits_total",
    "experience","education","employment_type","salary","position","working_hours","work_location",
    "start_datetime","end_datetime","application_method","application_format",
    "applicants_total","applicants_by_exp_new","applicants_by_exp_less_than_1yr","applicants_by_exp_1_3yrs","applicants_by_exp_3_5yrs","applicants_by_exp_over_5yrs",
    "applicants_by_salary_2200_2600","applicants_by_salary_2600_3000","applicants_by_salary_3000_4000","applicants_by_salary_over_4000",
    "applicants_by_gender_total","applicants_by_gender_male","applicants_by_gender_female","applicants_by_gender_ratio_male","applicants_by_gender_ratio_female",
    "applicants_by_age_20s","applicants_by_age_30s","applicants_by_age_40s","applicants_by_age_50s","applicants_by_age_over_60s",
    "applicants_by_education_highschool_or_less","applicants_by_education_associates","applicants_by_education_bachelors","applicants_by_education_masters","applicants_by_education_phd",
    "applicants_submitted_portfolio","saramin_posting_details_collection_time"
]
df_pd = df_pd.reindex(columns=cols)

# CSV 저장
csv_path = "/dbfs/FileStore/saramin_posting.csv"
df_pd.to_csv(csv_path, index=False, encoding="utf-8-sig")
print(f"CSV saved to {csv_path}")

# Delta 테이블 upsert
df_spark = spark.createDataFrame(df_pd)

spark.sql("""
CREATE TABLE IF NOT EXISTS brz_saramin_posting (
    posting_title STRING,
    company_name STRING,
    posting_id BIGINT,
    is_closed BOOLEAN,
    posting_bookmarks_total INT,
    posting_views_total INT,
    homepage_visits_total INT,
    experience STRING,
    education STRING,
    employment_type STRING,
    salary STRING,
    position STRING,
    working_hours STRING,
    work_location STRING,
    start_datetime STRING,
    end_datetime STRING,
    application_method STRING,
    application_format STRING,
    applicants_total INT,
    applicants_by_exp_new INT,
    applicants_by_exp_less_than_1yr INT,
    applicants_by_exp_1_3yrs INT,
    applicants_by_exp_3_5yrs INT,
    applicants_by_exp_over_5yrs INT,
    applicants_by_salary_2200_2600 INT,
    applicants_by_salary_2600_3000 INT,
    applicants_by_salary_3000_4000 INT,
    applicants_by_salary_over_4000 INT,
    applicants_by_gender_total INT,
    applicants_by_gender_male INT,
    applicants_by_gender_female INT,
    applicants_by_gender_ratio_male DOUBLE,
    applicants_by_gender_ratio_female DOUBLE,
    applicants_by_age_20s INT,
    applicants_by_age_30s INT,
    applicants_by_age_40s INT,
    applicants_by_age_50s INT,
    applicants_by_age_over_60s INT,
    applicants_by_education_highschool_or_less INT,
    applicants_by_education_associates INT,
    applicants_by_education_bachelors INT,
    applicants_by_education_masters INT,
    applicants_by_education_phd INT,
    applicants_submitted_portfolio INT,
    saramin_posting_details_collection_time STRING
)
USING DELTA
""")

target = DeltaTable.forName(spark, "brz_saramin_posting")
(target.alias("t")
 .merge(df_spark.alias("s"), "t.posting_id = s.posting_id")
 .whenMatchedUpdateAll()
 .whenNotMatchedInsertAll()
 .execute())

print("Upsert to brz_saramin_posting completed.")


https://www.saramin.co.kr/zf_user/auth
['searchword', 'id', 'id_save'] ['password']
id password


---------------------------------------------------------------------------
RuntimeError                              Traceback (most recent call last)
File <command-8079581274090009>, line 263
    257     return pd.DataFrame(rows)
    259 # ----- 입력 배열 준비 (이미 보유했다고 가정)
    260 # posting_id_array = np.array([51606407, 51687390, ...])
    261 
    262 # ----- 실행
--> 263 df_pd = crawl_with_login(posting_id_array)
    265 # 스키마/컬럼 순서 고정
    266 cols = [
    267     "posting_title","company_name","posting_id","is_closed",
    268     "posting_bookmarks_total","posting_views_total","homepage_visits_total",
   (...)
    276     "applicants_submitted_portfolio","saramin_posting_details_collection_time"
    277 ]

File <command-8079581274090009>, line 232, in crawl_with_login(posting_ids)
    231 def crawl_with_login(posting_ids: np.ndarray) -> pd.DataFrame:
--> 232     session = create_logged_in_session()
    233     rows = []
    234     for pid in posting_ids:

File <command-807958127409005

company_url_saramin 컬럼에 회사 상세 페이지 href(상대경로 → 절대 URL로 변환)를 저장하도록 코드만 깔끔히 추가

### import 추가

In [0]:
from urllib.parse import urljoin

### 파서: 회사 URL 추출 로직 추가 (parse_record)

로그인 버전/비로그인 버전 둘 다 parse_record만 위처럼 바꾸면 됩니다.

In [0]:
def parse_record(soup: BeautifulSoup, posting_id: int) -> Dict[str, Any]:
    title = clean_text(soup.select_one(".jv_header h1.tit_job").get_text(" ", strip=True)) if soup.select_one(".jv_header h1.tit_job") else None
    company = clean_text(soup.select_one(".jv_header .company").get_text(" ", strip=True)) if soup.select_one(".jv_header .company") else None

    # ⬇️ 추가: 회사 URL (title_inner 안의 a.company href)
    company_url = None
    a_company = soup.select_one(".title_inner a.company")
    if a_company and a_company.get("href"):
        company_url = urljoin("https://www.saramin.co.kr", a_company["href"])

    summary = parse_summary_keyvalue(soup)
    ...
    collected_at = datetime.now(SEOUL).strftime("%Y-%m-%d %H:%M:%S")

    return {
        "posting_title": title,
        "company_name": company,
        "company_url_saramin": company_url,   # ⬅️ 신규 컬럼
        "posting_id": int(posting_id),
        ...
        "saramin_posting_details_collection_time": collected_at
    }


  File <command-8079581274090019>, line 20
    ...
      ^
SyntaxError: ':' expected after dictionary key


### 컬럼 순서에 company_url_saramin 추가

기존 cols 리스트에서 company_name 다음에 넣어주세요. CSV는 자동으로 이 컬럼까지 포함되어 /dbfs/FileStore/saramin_posting.csv 로 저장됩니다.

In [0]:
cols = [
    "posting_title",
    "company_name",
    "company_url_saramin",   # ⬅️ 추가
    "posting_id",
    "is_closed",
    ...
    "saramin_posting_details_collection_time",
]


### Delta 테이블 스키마에 컬럼 추가

(A) 테이블이 아직 없다면: CREATE TABLE 정의에 컬럼 포함

In [0]:
%sql
CREATE TABLE IF NOT EXISTS brz_saramin_posting (
    posting_title STRING,
    company_name STRING,
    company_url_saramin STRING,  -- ⬅️ 추가
    posting_id BIGINT,
    is_closed BOOLEAN,
    posting_bookmarks_total INT,
    posting_views_total INT,
    homepage_visits_total INT,
    experience STRING,
    education STRING,
    employment_type STRING,
    salary STRING,
    position STRING,
    working_hours STRING,
    work_location STRING,
    start_datetime STRING,
    end_datetime STRING,
    application_method STRING,
    application_format STRING,
    applicants_total INT,
    applicants_by_exp_new INT,
    applicants_by_exp_less_than_1yr INT,
    applicants_by_exp_1_3yrs INT,
    applicants_by_exp_3_5yrs INT,
    applicants_by_exp_over_5yrs INT,
    applicants_by_salary_2200_2600 INT,
    applicants_by_salary_2600_3000 INT,
    applicants_by_salary_3000_4000 INT,
    applicants_by_salary_over_4000 INT,
    applicants_by_gender_total INT,
    applicants_by_gender_male INT,
    applicants_by_gender_female INT,
    applicants_by_gender_ratio_male DOUBLE,
    applicants_by_gender_ratio_female DOUBLE,
    applicants_by_age_20s INT,
    applicants_by_age_30s INT,
    applicants_by_age_40s INT,
    applicants_by_age_50s INT,
    applicants_by_age_over_60s INT,
    applicants_by_education_highschool_or_less INT,
    applicants_by_education_associates INT,
    applicants_by_education_bachelors INT,
    applicants_by_education_masters INT,
    applicants_by_education_phd INT,
    applicants_submitted_portfolio INT,
    saramin_posting_details_collection_time STRING
)
USING DELTA

(B) 테이블이 이미 있다면: 안전하게 컬럼 추가

In [0]:
try:
    spark.sql("ALTER TABLE brz_saramin_posting ADD COLUMNS (company_url_saramin STRING)")
except Exception as e:
    # 이미 존재하면 무시
    print("company_url_saramin column may already exist:", str(e))


In [0]:
df_spark = spark.createDataFrame(df_pd)
DeltaTable.forName(spark, "brz_saramin_posting") \
  .alias("t").merge(df_spark.alias("s"), "t.posting_id = s.posting_id") \
  .whenMatchedUpdateAll().whenNotMatchedInsertAll().execute()


를 실행하면 company_url_saramin까지 함께 upsert 됩니다.

%md
## 2) 기업정보, 기업연봉정보 상세페이지 크롤링

기업소개(1) + 연봉정보(2) 두 테이블을 company_url_saramin에서 따라가 로그인 후 수집하도록, 바로 붙여 넣어 실행 가능한 파이프라인을 정리했어요.
(아래 코드는 이전 단계에서 이미 로그인 세션을 쓰고 있다면 그대로 재사용합니다. 로그인 세션이 없다면 Selenium 방식으로 로그인하는 보조 함수를 포함해 두었습니다.)

### 설치(필요 시)

Databricks 등에서 Selenium을 쓸 경우에만 설치하세요.

In [0]:
pip install requests bs4 lxml python-dateutil pytz
# (선택) Selenium 사용할 때만
pip install selenium webdriver-manager


### 파서 & 크롤러 유틸 (기업소개 + 연봉정보)

메모: 연봉정보 탭이 없는 회사는 salrec이 None으로 떨어지며, 이 경우 두 번째 테이블 insert를 건너뜁니다.

In [0]:
import re, json, time, math
from typing import Optional, Dict, Any, Tuple
from urllib.parse import urljoin, urlparse, parse_qs
from datetime import datetime
import pytz
import requests
from bs4 import BeautifulSoup

SEOUL = pytz.timezone("Asia/Seoul")
BASE = "https://www.saramin.co.kr"

def now_kr():
    return datetime.now(SEOUL).strftime("%Y-%m-%d %H:%M:%S")

def to_int(x: Optional[str]) -> Optional[int]:
    if not x: return None
    x = re.sub(r"[^0-9\-]", "", x)
    if x in ("", "-"): return None
    try: return int(x)
    except: return None

def to_float(x: Optional[str]) -> Optional[float]:
    if not x: return None
    x = x.strip()
    x = x.replace("%","")
    x = re.sub(r"[^\-\d\.]", "", x)
    try: return float(x)
    except: return None

def sel_text(soup: BeautifulSoup, css: str, sep=" ", attr: Optional[str]=None) -> Optional[str]:
    el = soup.select_one(css)
    if not el: return None
    if attr:
        val = el.get(attr)
        return val.strip() if isinstance(val, str) else None
    return el.get_text(sep, strip=True)

def list_texts(soup: BeautifulSoup, css: str) -> list:
    return [e.get_text(" ", strip=True) for e in soup.select(css)]

def extract_json_after(pattern: str, html: str) -> Optional[dict]:
    """
    pattern: e.g. r'new EmployeeChart\((\{.*?\})\);'
    """
    m = re.search(pattern, html, re.S)
    if not m: return None
    try:
        return json.loads(m.group(1))
    except Exception:
        # 일부 페이지는 JS trailing comma 등으로 표준 JSON이 아닐 수 있어 정리
        cleaned = m.group(1)
        cleaned = re.sub(r",\s*}", "}", cleaned)
        cleaned = re.sub(r",\s*]", "]", cleaned)
        try:
            return json.loads(cleaned)
        except:
            return None

def extract_year_value_pairs_from_bar(wrapper: BeautifulSoup) -> Dict[str, Optional[int]]:
    """
    대졸초임 그래프처럼 <em class="tit_graph">2024</em> ... <span class="txt_value">3,592</span>
    구조를 [연도 -> 값] dict로 뽑는다.
    """
    out = {}
    for box in wrapper.select(".wrap_graph"):
        yr = sel_text(box, ".tit_graph")
        val = sel_text(box, ".graph .inner_graph .txt_value")
        if yr:
            out[yr] = to_int(val)
    return out

def parse_csn_from_url(url: str) -> Optional[str]:
    # /zf_user/company-info/view?csn=... 형식에서 csn 파라미터 추출
    try:
        q = parse_qs(urlparse(url).query)
        csn = q.get("csn", [None])[0]
        return csn
    except:
        return None

# -------------------------------
# (1) 기업소개 페이지 파싱
# -------------------------------
def parse_company_page(html: str, company_url: str) -> Dict[str, Any]:
    soup = BeautifulSoup(html, "lxml")

    # 회사명
    company_name = (sel_text(soup, "#companyinfo_company_nm") 
                    or sel_text(soup, "h1.tit_company"))

    # 관심기업 총합
    bookmarks_total_txt = sel_text(soup, "button.interested_corp span")
    company_bookmarks_total = to_int(bookmarks_total_txt)

    # 상단 인기도 카드(최근 1개월로 안내)
    # 조회수/관심기업/키워드검색 횟수, 증가율은 '관심기업'만 표기될 수 있음
    card = soup.select(".favor_company .favor_company_item")
    views_m = None
    views_inc_m = None
    bms_m = None
    bms_inc_m = None
    kw_m = None
    kw_inc_m = None

    for li in card:
        title = sel_text(li, ".tit")
        if not title: continue
        num = to_int(sel_text(li, ".counting .count .num"))
        pct = sel_text(li, ".counting .percent")
        pct_val = to_float(pct) if pct else None

        if "조회수" in title:
            views_m = num
            views_inc_m = pct_val
        elif "관심기업" in title:
            bms_m = num
            bms_inc_m = pct_val
        elif "키워드" in title:
            kw_m = num
            kw_inc_m = pct_val

    # 회사 키워드(사람인 제공)
    company_keywords_saramin = ", ".join(list_texts(soup, ".company_curation .company_curation_item .txt")) or None

    # 설립일
    founded_date = None
    founded_date = sel_text(soup, "#range_data", attr="data-establish_dt") or founded_date
    # 보이는 텍스트 예: "2020년 1월 15일 설립"도 보정 가능(선택)
    if not founded_date:
        founded_desc = sel_text(soup, ".company_summary .company_summary_item:nth-of-type(1) .company_summary_desc")
        if founded_desc:
            m = re.search(r"(\d{4})년\s*(\d{1,2})월\s*(\d{1,2})일", founded_desc)
            if m:
                y, M, d = m.groups()
                founded_date = f"{y}-{int(M):02d}-{int(d):02d}"

    # 기업형태
    # tooltip_company_type 안의 "기업형태: ..." 문구 우선
    company_type = None
    tip = soup.select_one(".tooltip_company_type .TipTxt")
    if tip:
        t = tip.get_text(" ", strip=True)
        t = re.sub(r"^.*기업형태\s*:\s*", "", t)
        company_type = t.strip()
    if not company_type:
        company_type = sel_text(soup, ".tooltip_company_type .company_summary_tit")

    # 매출액(없을 수 있음) → 상세 정보 그룹에서 '매출액'이 있으면 추출
    revenue = None
    for grp in soup.select(".company_details .company_details_group"):
        tit = sel_text(grp, ".tit")
        val = sel_text(grp, ".desc")
        if tit and val:
            if "매출" in tit or "매출액" in tit:
                revenue = val
                break

    # 업종, 대표, 홈페이지, 사업내용, 주소
    def detail_value(name_contains: str) -> Optional[str]:
        for grp in soup.select(".company_details .company_details_group"):
            tit = sel_text(grp, ".tit") or ""
            if name_contains in tit:
                # a 태그/텍스트 혼재 -> 전체 텍스트
                return sel_text(grp, ".desc")
        return None

    industry = (detail_value("업종") or sel_text(soup, ".box_title .txt_job"))
    ceo_name = detail_value("대표자명")
    homepage_url = None
    home_grp = None
    for grp in soup.select(".company_details .company_details_group"):
        tit = sel_text(grp, ".tit") or ""
        if "홈페이지" in tit:
            home_grp = grp
            break
    if home_grp:
        homepage_url = sel_text(home_grp, "a", attr="href") or sel_text(home_grp, ".desc")

    business_description = detail_value("사업내용")
    address = detail_value("주소")

    # 복리후생: 카테고리별 항목 모아 하나의 문자열(쉼표 구분)
    benefits = []
    for li in soup.select(".list_welfare .welfare_item"):
        items = [e.get_text(" ", strip=True) for e in li.select(".list_welfare_cate .cate_item")]
        benefits.extend(items)
    company_benefits = ", ".join(benefits) if benefits else None

    # 사원수(요약 or 하단 '전체 사원수')
    employees_total = None
    # 우선 하단 표기
    employees_total = to_int(sel_text(soup, ".worker_info .col .value .num")) or employees_total
    # 요약카드의 '사원수'
    if employees_total is None:
        for it in soup.select(".company_summary .company_summary_item"):
            if "사원수" in (sel_text(it, ".company_summary_desc") or ""):
                employees_total = to_int(sel_text(it, ".company_summary_tit"))
                break

    # 인원 추이 JSON (new EmployeeChart({...}))
    emp_json = extract_json_after(r"new\s+EmployeeChart\((\{.*?\})\)", html)
    employees_timeseries_json = json.dumps(emp_json, ensure_ascii=False) if emp_json else None

    return {
        "company_name": company_name,
        "company_bookmarks_total": company_bookmarks_total,
        "company_views_monthly": views_m,
        "company_view_increase_rate_monthly": views_inc_m,
        "company_bookmarks_monthly": bms_m,
        "company_bookmark_increase_rate_monthly": bms_inc_m,
        "company_keyword_search_count_monthly": kw_m,
        "company_keyword_search_increase_rate_monthly": kw_inc_m,
        "company_keywords_saramin": company_keywords_saramin,
        "founded_date": founded_date,
        "company_type": company_type,
        "revenue": revenue,
        "industry": industry,
        "ceo_name": ceo_name,
        "homepage_url": homepage_url,
        "business_description": business_description,
        "address": address,
        "company_benefits": company_benefits,
        "employees_total": employees_total,
        "employees_timeseries_json": employees_timeseries_json,
        "company_url_saramin": urljoin(BASE, company_url),
        "saramin_company_details_collection_time": now_kr(),
    }

# -------------------------------
# (2) 연봉정보 탭 파싱
# -------------------------------
def find_salary_url_on_company_page(soup: BeautifulSoup, company_url: str) -> Optional[str]:
    # 네비게이션 버튼에서 '연봉정보' 버튼 href
    for btn in soup.select(".company_navi .btn_menu"):
        txt = btn.get_text(" ", strip=True)
        if "연봉정보" in txt:
            # onclick="window.location.href='/zf_user/company-info/view-inner-salary?csn=...';"
            oc = btn.get("onclick") or ""
            m = re.search(r"href\s*=\s*'([^']+)'", oc)
            if m:
                return urljoin(BASE, m.group(1))
    # 하단 바로가기 링크
    direct = soup.select_one("a.link_content_more[href*='view-inner-salary']")
    if direct and direct.get("href"):
        return urljoin(BASE, direct["href"])
    # csn 기반 추정
    csn = (sel_text(soup, "#companyinfo_view_csn", attr="value")
           or parse_csn_from_url(company_url))
    if csn:
        return f"{BASE}/zf_user/company-info/view-inner-salary?csn={csn}"
    return None

def parse_salary_page(html: str, salary_url: str, company_name_fallback: Optional[str]=None) -> Dict[str, Any]:
    soup = BeautifulSoup(html, "lxml")

    # 회사명
    company_name = sel_text(soup, "#company_name") or company_name_fallback

    # 평균연봉 섹션
    salary_avg = to_int(sel_text(soup, ".salary_avg .average_currency em"))
    salary_min = to_int(sel_text(soup, ".salary_avg .aver_bar .min_txt em"))
    salary_max = to_int(sel_text(soup, ".salary_avg .aver_bar .max_txt em"))
    salary_yoy_change = to_float(sel_text(soup, ".salary_avg .textinfo .info:nth-of-type(1) .point em"))
    salary_info_reliability = sel_text(soup, ".salary_avg .textinfo .reliability .gauge")

    # setCombinationChart(...) JSON (연도별 평균/업종평균)
    combo = extract_json_after(r"setCombinationChart\((\{.*?\})\)", html)
    yrs = {str(x.get("years")): x for x in (combo or {}).get("average_years_salary", [])}

    def yr_val(year: str, key: str) -> Optional[int]:
        v = (yrs.get(year) or {}).get(key)
        return int(v) if v is not None else None

    salary_2021_avg = yr_val("2021", "avg_salary")
    salary_2021_min = yr_val("2021", "min_salary")
    salary_2021_max = yr_val("2021", "max_salary")
    salary_2022_avg = yr_val("2022", "avg_salary")
    salary_2022_min = yr_val("2022", "min_salary")
    salary_2022_max = yr_val("2022", "max_salary")
    salary_2023_avg = yr_val("2023", "avg_salary")
    salary_2023_min = yr_val("2023", "min_salary")
    salary_2023_max = yr_val("2023", "max_salary")

    salary_2021_avg_industry = yr_val("2021", "same_kind_avg_salary")
    salary_2022_avg_industry = yr_val("2022", "same_kind_avg_salary")
    salary_2023_avg_industry = yr_val("2023", "same_kind_avg_salary")

    # 대졸초임
    starting_salary_bachelors_avg = to_int(sel_text(soup, ".salary_college .salary_graph_info .salary em"))
    keypoint = sel_text(soup, ".salary_college .salary_graph_info .keypoint")
    # 예: "3.52% 하락" → -3.52, "2.31% 상승" → +2.31
    starting_salary_bachelors_yoy_change = None
    if keypoint:
        m = re.search(r"([\-]?\d+(?:\.\d+)?)\s*%\s*(상승|하락)", keypoint)
        if m:
            v = float(m.group(1))
            if "하락" in m.group(2):
                v = -abs(v)
            starting_salary_bachelors_yoy_change = v

    # 대졸초임 연도별 바
    col_wrap = soup.select_one(".salary_college .graph_info")
    cvals = extract_year_value_pairs_from_bar(col_wrap) if col_wrap else {}
    starting_salary_bachelors_2021_avg = cvals.get("2021")
    starting_salary_bachelors_2022_avg = cvals.get("2022")
    starting_salary_bachelors_2023_avg = cvals.get("2023")

    # (예상 월 실수령액)
    takehome = to_int(sel_text(soup, ".salary_college .salary_graph_info .expected strong"))

    # 직급별 연봉통계 (사원/주임/대리/과장/차장/부장)
    # 각각 dl.row에 평균, 구간(min/max) 존재
    def parse_row_avg_min_max(title_contains: str) -> Tuple[Optional[int], Optional[int], Optional[int]]:
        for row in soup.select("#positon_list_div dl.row"):
            title = sel_text(row, ".title") or ""
            if title_contains in title:
                avg = to_int(sel_text(row, ".index"))
                rng = row.select_one(".innerbar")
                if rng:
                    # 예: <span class="min"><em>최저</em> 3,125</span>
                    rmin = to_int(sel_text(rng, ".min"))
                    rmax = to_int(sel_text(rng, ".max"))
                else:
                    rmin = rmax = None
                return avg, rmin, rmax
        return None, None, None

    salary_staff_high_school_avg, salary_staff_high_school_min, salary_staff_high_school_max = parse_row_avg_min_max("사원 (고졸)")
    salary_staff_associates_avg,  salary_staff_associates_min,  salary_staff_associates_max  = parse_row_avg_min_max("사원-대졸(2,3년)")
    salary_staff_bachelors_avg,   salary_staff_bachelors_min,   salary_staff_bachelors_max   = parse_row_avg_min_max("사원-대졸(4년)")
    salary_junior_mgr_avg,        salary_junior_mgr_min,        salary_junior_mgr_max        = parse_row_avg_min_max("주임")
    salary_deputy_mgr_avg,        salary_deputy_mgr_min,        salary_deputy_mgr_max        = parse_row_avg_min_max("대리")
    salary_section_chief_avg,     salary_section_chief_min,     salary_section_chief_max     = parse_row_avg_min_max("과장")
    salary_deputy_section_chief_avg, salary_deputy_section_chief_min, salary_deputy_section_chief_max = parse_row_avg_min_max("차장")
    salary_department_head_avg,   salary_department_head_min,   salary_department_head_max   = parse_row_avg_min_max("부장")

    # 연령별 연봉통계 JSON
    line = extract_json_after(r"setLineChart\((\{.*?\})\)", html)
    by_age = (line or {}).get("list", {}).get("salary", {})
    salary_by_age_2021_json = json.dumps(by_age.get("2021"), ensure_ascii=False) if "2021" in by_age else None
    salary_by_age_2022_json = json.dumps(by_age.get("2022"), ensure_ascii=False) if "2022" in by_age else None
    salary_by_age_2023_json = json.dumps(by_age.get("2023"), ensure_ascii=False) if "2023" in by_age else None

    return {
        "company_name": company_name,
        "salary_avg": salary_avg,
        "salary_min": salary_min,
        "salary_max": salary_max,
        "salary_yoy_change": salary_yoy_change,
        "salary_info_reliability": salary_info_reliability,
        "salary_2021_avg": salary_2021_avg,
        "salary_2021_min": salary_2021_min,
        "salary_2021_max": salary_2021_max,
        "salary_2022_avg": salary_2022_avg,
        "salary_2022_min": salary_2022_min,
        "salary_2022_max": salary_2022_max,
        "salary_2023_avg": salary_2023_avg,
        "salary_2023_min": salary_2023_min,
        "salary_2023_max": salary_2023_max,
        "salary_2021_avg_industry": salary_2021_avg_industry,
        "salary_2022_avg_industry": salary_2022_avg_industry,
        "salary_2023_avg_industry": salary_2023_avg_industry,
        "starting_salary_bachelors_avg": starting_salary_bachelors_avg,
        "starting_salary_bachelors_yoy_change": starting_salary_bachelors_yoy_change,
        "starting_salary_bachelors_2021_avg": starting_salary_bachelors_2021_avg,
        "starting_salary_bachelors_2022_avg": starting_salary_bachelors_2022_avg,
        "starting_salary_bachelors_2023_avg": starting_salary_bachelors_2023_avg,
        "starting_salary_bachelors_estimated_monthly_takehome": takehome,
        "salary_staff_high_school_avg": salary_staff_high_school_avg,
        "salary_staff_high_school_min": salary_staff_high_school_min,
        "salary_staff_high_school_max": salary_staff_high_school_max,
        "salary_staff_associates_avg": salary_staff_associates_avg,
        "salary_staff_associates_min": salary_staff_associates_min,
        "salary_staff_associates_max": salary_staff_associates_max,
        "salary_staff_bachelors_avg": salary_staff_bachelors_avg,
        "salary_staff_bachelors_min": salary_staff_bachelors_min,
        "salary_staff_bachelors_max": salary_staff_bachelors_max,
        "salary_junior_mgr_avg": salary_junior_mgr_avg,
        "salary_junior_mgr_min": salary_junior_mgr_min,
        "salary_junior_mgr_max": salary_junior_mgr_max,
        "salary_deputy_mgr_avg": salary_deputy_mgr_avg,
        "salary_deputy_mgr_min": salary_deputy_mgr_min,
        "salary_deputy_mgr_max": salary_deputy_mgr_max,
        "salary_section_chief_avg": salary_section_chief_avg,
        "salary_section_chief_min": salary_section_chief_min,
        "salary_section_chief_max": salary_section_chief_max,
        "salary_deputy_section_chief_avg": salary_deputy_section_chief_avg,
        "salary_deputy_section_chief_min": salary_deputy_section_chief_min,
        "salary_deputy_section_chief_max": salary_deputy_section_chief_max,
        "salary_department_head_avg": salary_department_head_avg,
        "salary_department_head_min": salary_department_head_min,
        "salary_department_head_max": salary_department_head_max,
        "salary_by_age_2021_json": salary_by_age_2021_json,
        "salary_by_age_2022_json": salary_by_age_2022_json,
        "salary_by_age_2023_json": salary_by_age_2023_json,
        "company_salary_url_saramin": urljoin(BASE, salary_url) if salary_url else None,
        "saramin_company_salary_collection_time": now_kr(),
    }

# -------------------------------
# (3) 로그인 + 페이지 GET
# -------------------------------
def get_logged_session(email: str, password: str) -> requests.Session:
    """
    기존에 쓰시던 로그인 세션 재활용을 권장합니다.
    이 함수는 requests 세션을 기본 구성만 합니다. 
    (사이트 측 로그인 파라미터/토큰이 바뀔 수 있어 실제 로그인 엔드포인트는 귀사 코드와 맞추세요.)
    """
    sess = requests.Session()
    sess.headers.update({
        "User-Agent": "Mozilla/5.0"
    })
    # ※ 이미 로그인 로직이 있다면 그 함수를 사용하세요.
    # 예시:
    # login_page = sess.get(f"{BASE}/zf_user/member/login")
    # csrftoken 추출 -> payload 구성 -> sess.post(login_submit_url, data=payload)
    return sess

def fetch_html(sess: requests.Session, url: str) -> str:
    r = sess.get(url, timeout=30)
    r.raise_for_status()
    return r.text

def scrape_company_and_salary(sess: requests.Session, company_url: str, fetch_salary_if_exists: bool=True
                              ) -> Tuple[Dict[str, Any], Optional[Dict[str, Any]]]:
    # 1) 기업소개
    company_url_abs = urljoin(BASE, company_url)
    html_company = fetch_html(sess, company_url_abs)
    comp = parse_company_page(html_company, company_url_abs)

    # 2) 연봉정보(버튼 있는 경우만)
    salrec = None
    if fetch_salary_if_exists:
        soup = BeautifulSoup(html_company, "lxml")
        salary_url = find_salary_url_on_company_page(soup, company_url_abs)
        if salary_url:
            html_salary = fetch_html(sess, salary_url)
            salrec = parse_salary_page(html_salary, salary_url, comp.get("company_name"))
    return comp, salrec


### Delta 테이블 스키마 생성(최초 1회)

In [0]:
-- (1) 기업소개 테이블
CREATE TABLE IF NOT EXISTS brz_saramin_company (
  company_name STRING,
  company_bookmarks_total INT,
  company_views_monthly INT,
  company_view_increase_rate_monthly DOUBLE,
  company_bookmarks_monthly INT,
  company_bookmark_increase_rate_monthly DOUBLE,
  company_keyword_search_count_monthly INT,
  company_keyword_search_increase_rate_monthly DOUBLE,
  company_keywords_saramin STRING,
  founded_date STRING,
  company_type STRING,
  revenue STRING,
  industry STRING,
  ceo_name STRING,
  homepage_url STRING,
  business_description STRING,
  address STRING,
  company_benefits STRING,
  employees_total INT,
  employees_timeseries_json STRING,
  company_url_saramin STRING,
  saramin_company_details_collection_time STRING
)
USING DELTA;

-- (2) 연봉정보 테이블
CREATE TABLE IF NOT EXISTS brz_saramin_company_salary (
  company_name STRING,
  salary_avg INT,
  salary_min INT,
  salary_max INT,
  salary_yoy_change DOUBLE,
  salary_info_reliability STRING,
  salary_2021_avg INT,
  salary_2021_min INT,
  salary_2021_max INT,
  salary_2022_avg INT,
  salary_2022_min INT,
  salary_2022_max INT,
  salary_2023_avg INT,
  salary_2023_min INT,
  salary_2023_max INT,
  salary_2021_avg_industry INT,
  salary_2022_avg_industry INT,
  salary_2023_avg_industry INT,
  starting_salary_bachelors_avg INT,
  starting_salary_bachelors_yoy_change DOUBLE,
  starting_salary_bachelors_2021_avg INT,
  starting_salary_bachelors_2022_avg INT,
  starting_salary_bachelors_2023_avg INT,
  starting_salary_bachelors_estimated_monthly_takehome INT,
  salary_staff_high_school_avg INT,
  salary_staff_high_school_min INT,
  salary_staff_high_school_max INT,
  salary_staff_associates_avg INT,
  salary_staff_associates_min INT,
  salary_staff_associates_max INT,
  salary_staff_bachelors_avg INT,
  salary_staff_bachelors_min INT,
  salary_staff_bachelors_max INT,
  salary_junior_mgr_avg INT,
  salary_junior_mgr_min INT,
  salary_junior_mgr_max INT,
  salary_deputy_mgr_avg INT,
  salary_deputy_mgr_min INT,
  salary_deputy_mgr_max INT,
  salary_section_chief_avg INT,
  salary_section_chief_min INT,
  salary_section_chief_max INT,
  salary_deputy_section_chief_avg INT,
  salary_deputy_section_chief_min INT,
  salary_deputy_section_chief_max INT,
  salary_department_head_avg INT,
  salary_department_head_min INT,
  salary_department_head_max INT,
  salary_by_age_2021_json STRING,
  salary_by_age_2022_json STRING,
  salary_by_age_2023_json STRING,
  company_salary_url_saramin STRING,
  saramin_company_salary_collection_time STRING
)
USING DELTA;


### 배치 수집 실행 (Spark + Delta upsert)

이미 만들어 둔 공고 테이블/데이터프레임에서 company_url_saramin 고유값만 뽑아 돌립니다.

merge 키는 기업소개: company_url_saramin, 연봉정보: company_salary_url_saramin 으로 했습니다.

**동작 포인트 & 예외 처리**

연봉정보 버튼이 없는 회사: salary_rows에 안 들어갑니다(두 번째 테이블 insert 스킵).

일부 필드 부재: 파서는 안전하게 None으로 채워둡니다.

증감률 텍스트: "하락"이면 음수, "상승"이면 양수로 변환합니다.

사원수 추이 / 연령별·연도별 급여: 페이지 내 JS의 JSON을 정규식으로 안전 추출합니다.

merge 키:
- brz_saramin_company → company_url_saramin
- brz_saramin_company_salary → company_salary_url_saramin

In [0]:
import pandas as pd
from delta.tables import DeltaTable

# 1) 로그인 세션 만들기 (기존 세션 재활용 가능)
EMAIL = "nulimi7@gmail.com"
PASSWORD = "snflalTHD7!"
session = get_logged_session(EMAIL, PASSWORD)

# 2) 수집 대상 URL 준비 (예: 공고 테이블에서 distinct)
posting_tbl = "brz_saramin_posting"   # 이름 다르면 바꿔주세요
post_df = spark.table(posting_tbl).select("company_url_saramin").dropna().dropDuplicates()
company_urls = [r.company_url_saramin for r in post_df.collect()]

company_rows = []
salary_rows = []

for url in company_urls:
    try:
        comp, sal = scrape_company_and_salary(session, url, fetch_salary_if_exists=True)
        if comp: company_rows.append(comp)
        if sal:  salary_rows.append(sal)
    except Exception as e:
        print(f"[WARN] company scrape failed: {url} -> {e}")

# 3) Spark DF 변환
company_pd = pd.DataFrame(company_rows) if company_rows else pd.DataFrame(columns=[
    "company_name","company_bookmarks_total","company_views_monthly",
    "company_view_increase_rate_monthly","company_bookmarks_monthly",
    "company_bookmark_increase_rate_monthly","company_keyword_search_count_monthly",
    "company_keyword_search_increase_rate_monthly","company_keywords_saramin",
    "founded_date","company_type","revenue","industry","ceo_name","homepage_url",
    "business_description","address","company_benefits","employees_total",
    "employees_timeseries_json","company_url_saramin","saramin_company_details_collection_time"
])

salary_pd = pd.DataFrame(salary_rows) if salary_rows else pd.DataFrame(columns=[
    "company_name","salary_avg","salary_min","salary_max","salary_yoy_change",
    "salary_info_reliability","salary_2021_avg","salary_2021_min","salary_2021_max",
    "salary_2022_avg","salary_2022_min","salary_2022_max","salary_2023_avg",
    "salary_2023_min","salary_2023_max","salary_2021_avg_industry","salary_2022_avg_industry",
    "salary_2023_avg_industry","starting_salary_bachelors_avg","starting_salary_bachelors_yoy_change",
    "starting_salary_bachelors_2021_avg","starting_salary_bachelors_2022_avg",
    "starting_salary_bachelors_2023_avg","starting_salary_bachelors_estimated_monthly_takehome",
    "salary_staff_high_school_avg","salary_staff_high_school_min","salary_staff_high_school_max",
    "salary_staff_associates_avg","salary_staff_associates_min","salary_staff_associates_max",
    "salary_staff_bachelors_avg","salary_staff_bachelors_min","salary_staff_bachelors_max",
    "salary_junior_mgr_avg","salary_junior_mgr_min","salary_junior_mgr_max",
    "salary_deputy_mgr_avg","salary_deputy_mgr_min","salary_deputy_mgr_max",
    "salary_section_chief_avg","salary_section_chief_min","salary_section_chief_max",
    "salary_deputy_section_chief_avg","salary_deputy_section_chief_min","salary_deputy_section_chief_max",
    "salary_department_head_avg","salary_department_head_min","salary_department_head_max",
    "salary_by_age_2021_json","salary_by_age_2022_json","salary_by_age_2023_json",
    "company_salary_url_saramin","saramin_company_salary_collection_time"
])

company_sdf = spark.createDataFrame(company_pd)
salary_sdf  = spark.createDataFrame(salary_pd)

# 4) Delta upsert
DeltaTable.forName(spark, "brz_saramin_company") \
  .alias("t").merge(company_sdf.alias("s"), "t.company_url_saramin = s.company_url_saramin") \
  .whenMatchedUpdateAll().whenNotMatchedInsertAll().execute()

DeltaTable.forName(spark, "brz_saramin_company_salary") \
  .alias("t").merge(salary_sdf.alias("s"), "t.company_salary_url_saramin = s.company_salary_url_saramin") \
  .whenMatchedUpdateAll().whenNotMatchedInsertAll().execute()


#3. 테이블 확인

#4. DB 적재

3개 테이블(brz_saramin_posting, brz_saramin_company, brz_saramin_company_salary)의 스키마와, DF를 스키마에 맞춰 캐스팅한 뒤 JDBC로 적재하는 예시예요. {schema}는 bronze로 씁니다.

Postgres bronze 스키마가 없다면 먼저 만들어 주세요:

In [0]:
%sql
CREATE SCHEMA IF NOT EXISTS bronze;

정수/실수 컬럼은 Spark의 IntegerType/DoubleType → Postgres INTEGER/DOUBLE PRECISION으로 매핑됩니다.

JSON 컬럼은 문자열로 저장(TEXT/VARCHAR)하며, 필요하면 Postgres에서 ::jsonb 캐스팅해 활용하시면 됩니다.

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.types import (
    StructType, StructField, StringType, IntegerType, DoubleType
)

# 1) 스키마 정의 -----------------------------------------------------------
schema_brz_saramin_posting = StructType([
    # 공고 테이블은 최소 예시 컬럼입니다. 실제 파이프라인 컬럼에 맞춰 추가/삭제하세요.
    StructField("job_title", StringType(), True),
    StructField("job_url", StringType(), True),
    StructField("company_name", StringType(), True),
    StructField("company_url_saramin", StringType(), True),  # <- class="title_inner"에서 추출한 값
    StructField("collected_at", StringType(), True),
])

schema_brz_saramin_company = StructType([
    StructField("company_name", StringType(), True),
    StructField("company_bookmarks_total", IntegerType(), True),
    StructField("company_views_monthly", IntegerType(), True),
    StructField("company_view_increase_rate_monthly", DoubleType(), True),
    StructField("company_bookmarks_monthly", IntegerType(), True),
    StructField("company_bookmark_increase_rate_monthly", DoubleType(), True),
    StructField("company_keyword_search_count_monthly", IntegerType(), True),
    StructField("company_keyword_search_increase_rate_monthly", DoubleType(), True),
    StructField("company_keywords_saramin", StringType(), True),
    StructField("founded_date", StringType(), True),
    StructField("company_type", StringType(), True),
    StructField("revenue", StringType(), True),
    StructField("industry", StringType(), True),
    StructField("ceo_name", StringType(), True),
    StructField("homepage_url", StringType(), True),
    StructField("business_description", StringType(), True),
    StructField("address", StringType(), True),
    StructField("company_benefits", StringType(), True),
    StructField("employees_total", IntegerType(), True),
    StructField("employees_timeseries_json", StringType(), True),
    StructField("company_url_saramin", StringType(), True),
    StructField("saramin_company_details_collection_time", StringType(), True),
])

schema_brz_saramin_company_salary = StructType([
    StructField("company_name", StringType(), True),
    StructField("salary_avg", IntegerType(), True),
    StructField("salary_min", IntegerType(), True),
    StructField("salary_max", IntegerType(), True),
    StructField("salary_yoy_change", DoubleType(), True),
    StructField("salary_info_reliability", StringType(), True),
    StructField("salary_2021_avg", IntegerType(), True),
    StructField("salary_2021_min", IntegerType(), True),
    StructField("salary_2021_max", IntegerType(), True),
    StructField("salary_2022_avg", IntegerType(), True),
    StructField("salary_2022_min", IntegerType(), True),
    StructField("salary_2022_max", IntegerType(), True),
    StructField("salary_2023_avg", IntegerType(), True),
    StructField("salary_2023_min", IntegerType(), True),
    StructField("salary_2023_max", IntegerType(), True),
    StructField("salary_2021_avg_industry", IntegerType(), True),
    StructField("salary_2022_avg_industry", IntegerType(), True),
    StructField("salary_2023_avg_industry", IntegerType(), True),
    StructField("starting_salary_bachelors_avg", IntegerType(), True),
    StructField("starting_salary_bachelors_yoy_change", DoubleType(), True),
    StructField("starting_salary_bachelors_2021_avg", IntegerType(), True),
    StructField("starting_salary_bachelors_2022_avg", IntegerType(), True),
    StructField("starting_salary_bachelors_2023_avg", IntegerType(), True),
    StructField("starting_salary_bachelors_estimated_monthly_takehome", IntegerType(), True),
    StructField("salary_staff_high_school_avg", IntegerType(), True),
    StructField("salary_staff_high_school_min", IntegerType(), True),
    StructField("salary_staff_high_school_max", IntegerType(), True),
    StructField("salary_staff_associates_avg", IntegerType(), True),
    StructField("salary_staff_associates_min", IntegerType(), True),
    StructField("salary_staff_associates_max", IntegerType(), True),
    StructField("salary_staff_bachelors_avg", IntegerType(), True),
    StructField("salary_staff_bachelors_min", IntegerType(), True),
    StructField("salary_staff_bachelors_max", IntegerType(), True),
    StructField("salary_junior_mgr_avg", IntegerType(), True),
    StructField("salary_junior_mgr_min", IntegerType(), True),
    StructField("salary_junior_mgr_max", IntegerType(), True),
    StructField("salary_deputy_mgr_avg", IntegerType(), True),
    StructField("salary_deputy_mgr_min", IntegerType(), True),
    StructField("salary_deputy_mgr_max", IntegerType(), True),
    StructField("salary_section_chief_avg", IntegerType(), True),
    StructField("salary_section_chief_min", IntegerType(), True),
    StructField("salary_section_chief_max", IntegerType(), True),
    StructField("salary_deputy_section_chief_avg", IntegerType(), True),
    StructField("salary_deputy_section_chief_min", IntegerType(), True),
    StructField("salary_deputy_section_chief_max", IntegerType(), True),
    StructField("salary_department_head_avg", IntegerType(), True),
    StructField("salary_department_head_min", IntegerType(), True),
    StructField("salary_department_head_max", IntegerType(), True),
    StructField("salary_by_age_2021_json", StringType(), True),
    StructField("salary_by_age_2022_json", StringType(), True),
    StructField("salary_by_age_2023_json", StringType(), True),
    StructField("company_salary_url_saramin", StringType(), True),
    StructField("saramin_company_salary_collection_time", StringType(), True),
])

schemas = {
    "brz_saramin_posting": schema_brz_saramin_posting,
    "brz_saramin_company": schema_brz_saramin_company,
    "brz_saramin_company_salary": schema_brz_saramin_company_salary,
}

# 2) DF를 스키마에 맞춰 정렬/캐스팅하는 유틸 ------------------------------
def align_to_schema(df, schema: StructType):
    cols = []
    for f in schema.fields:
        if f.name in df.columns:
            cols.append(F.col(f.name).cast(f.dataType).alias(f.name))
        else:
            cols.append(F.lit(None).cast(f.dataType).alias(f.name))
    return df.select(*cols)

# 3) JDBC 설정 -------------------------------------------------------------
jdbc_user = "postgres"
jdbc_pass = "asdASD123!@#"
host = "20.196.145.211"
port = "5432"
jdbc_url = f"jdbc:postgresql://{host}:{port}/postgres"
schema = "bronze"   # 요구사항대로 고정
mode = "append"     # 필요시 "overwrite" 등 변경

# 4) 쓰기 예시 -------------------------------------------------------------
# 예: posting_df, company_df, salary_df가 이미 존재한다고 가정
for table, df in [
    ("brz_saramin_posting", posting_df),
    ("brz_saramin_company", company_df),
    ("brz_saramin_company_salary", salary_df),
]:
    data = align_to_schema(df, schemas[table])   # 스키마 맞추기
    data.write.format("jdbc").mode(mode).options(
        url=jdbc_url,
        user=jdbc_user,
        password=jdbc_pass,
        dbtable=f"{schema}.{table}"
    ).save()
